# Juliaで学ぶ古典モンテカルロシミュレーション
## イジング模型のモンテカルロシミュレーション
さて、重みつきモンテカルロ法について色々調べたので、次は実際にイジング模型でシミュレーションを実行してみよう。  
プログラムを順番に作っていきながら、磁化のヒストグラムやスピン分布のアニメーションを作る。



まず、イジング模型をおさらいする。
## ハミルトニアンと分配関数
まず、古典スピン系であるイジング模型のハミルトニアンは
$$
H = -J \sum_{\langle i j \rangle} \sigma_i \sigma_j - h \sum_i \sigma_i
$$
である。第二項は磁場の効果である。ここで、$\langle i j \rangle$は、最隣接格子点のみで和を取ることを意味しており、一次元系であれば、$j=i+1$などである。
$\sigma_i$は$i$番目の格子点のスピンを表し、$+1$か$-1$を取る。  
統計力学において、物理量$A$の期待値は
$$
\langle A \rangle = \frac{1}{Z} \sum_{\cal C} \left[ \exp \left( -\frac{H({\cal C})}{k_{\rm B} T} \right) A({\cal C}) \right]
$$
と書ける。ここで、$H({\cal C})$は、あるスピン配置${\cal C}$でのハミルトニアン、$A({\cal C})$はその時の物理量$A$の値である。
$k_{\rm B}$はボルツマン定数、$T$は温度である。
$Z$は分配関数であり、
$$
Z = \sum_{\cal C}\exp \left( -\frac{H({\cal C})}{k_{\rm B} T} \right)
$$
と定義されている。  
つまり、すべての可能なスピン配置に関して和を取れば、物理量が計算できる。  
すべての可能なスピン配置の数${\cal N}$は、$N$個の格子点を持つ系の場合、各サイトで$-1$か$1$の二通りの状態を取れるので、
$$
{\cal N} = 2^N
$$
である。
## 二次元イジング模型
$L_x \times L_y$の正方格子の二次元イジング模型を考えよう。この時、あるサイトを${\bf i} = (i_x,i_y)$とすると、
その最近接格子は、
$$
{\bf d}_1 = (i_x+1,i_y),{\bf d}_2 = (i_x-1,i_y),{\bf d}_3 = (i_x,i_y+1), {\bf d}_4 = (i_x,i_y-1)
$$
の4点である。この時、イジング模型は
$$
H = -\frac{J}{2} \sum_{\bf i}^{L_x L_y} \sum_{l=1}^4 \sigma_{\bf i} \sigma_{{\bf i} + {\bf d}_l}- h \sum_{\bf i} \sigma_{\bf i}
$$
となる。ここで、本来一つしかない$\sigma_1 \sigma_2$を$\sigma_1 \sigma_2 = (\sigma_1 \sigma_2 + \sigma_2 \sigma_1)/2$と
分離したため、$1/2$の因子が先頭についた。そして
これは、
$$
H = -\frac{J}{2} \sum_{\bf i}^{L_x L_y} \sigma_{\bf i} \sum_{l=1}^4 \sigma_{{\bf i} + {\bf d}_l}- h \sum_{\bf i} \sigma_{\bf i}
$$
$$
= -\frac{J}{2} \sum_{\bf i}^{L_x L_y} \sigma_{\bf i} S_i - h \sum_{\bf i} \sigma_{\bf i}
$$
$$
S_i = \sum_{l=1}^4 \sigma_{{\bf i} + {\bf d}_l}
$$
と書くことができる。よって、あるサイト${\bf i}$の隣接格子点におけるスピンの和$S_i$がそれぞれわかれば、全エネルギー$H$を計算できる。  

あるサイト${\bf i}$の一つのスピンをフリップ$(\sigma_{\bf i} \rightarrow -\sigma_{\bf i})$した時、そのエネルギー差$\Delta E$は
$$
\Delta E = 2J \sigma_{\bf i} S_i+ 2h  \sigma_{\bf i}
$$
となる。
#### 1次元の例
周期境界条件を持つ4格子からなる1次元のイジング模型を考える。簡単のため磁場はゼロ($h=0$)とする。この時、ハミルトニアンは
$$
H = -J (\sigma_1 \sigma_2 + \sigma_1 \sigma_4 + \sigma_2 \sigma_3 + \sigma_3 \sigma_4)
$$
である。これは、
$$
H = -\frac{J}{2} (\sigma_1 \sigma_2 + \sigma_2 \sigma_1 + \sigma_1 \sigma_4 + \sigma_4 \sigma_1 + \sigma_2 \sigma_3 + \sigma_3 \sigma_2 +  \sigma_3 \sigma_4+ \sigma_4 \sigma_3)
$$
$$
= -\frac{J}{2} \left( \sigma_1 (\sigma_2 + \sigma_4) + \sigma_2 (\sigma_1 + \sigma_3) + \sigma_3 (\sigma_4 + \sigma_2) + \sigma_4 (\sigma_1 + \sigma_3)\right)
$$
のように、$i$を固定して隣接格子の和をとったものに変更できる。  
また、サイト$2$をフリップした場合は、エネルギーは
$$
H' = -J (-\sigma_1 \sigma_2 + \sigma_1 \sigma_4 - \sigma_2 \sigma_3 + \sigma_3 \sigma_4)
$$
となり、その差は
$$
H'-H = -J (-2\sigma_1 \sigma_2 - 2\sigma_2 \sigma_3 ) = 2J \sigma_2 (\sigma_1 + \sigma_3) 
$$
となり、ちゃんと上で計算した$\Delta E$となっている。
### 隣接格子点の情報
まず、隣接格子点を求める関数を


In [1]:
function 隣接格子点(ix,iy,Lx,Ly,周期境界)
    const lmax = 4 #最近接格子点の数
    ls = Array{Array{Int64,1}}(lmax)
    ds = ((+1,0),(-1,0),(0,+1),(0,-1))
    count = 0
    for d in ds        
        jx = ix + d[1]
        jy = iy + d[2]
        
        if 周期境界
            jx += ifelse(jx>Lx,-Lx,0)
            jx += ifelse(jx<1,Lx,0)    
            jy += ifelse(jy>Ly,-Ly,0)
            jy += ifelse(jy<1,Ly,0)                                  
        end     
        
        if 1 <= jx <= Lx && 1 <= jy <= Ly
            count += 1
            ls[count] = [jx,jy]
        end        
    end    
    return ls[1:count]

end

隣接格子点 (generic function with 1 method)

と定義しよう。これは、サイト${\bf i}$が与えられた時、${\bf i} + {\bf d}_l$の四つを返す。  
そして、あるサイト${\bf i}$の周辺スピンの和を

In [2]:
function 周辺スピン和(ix,iy,Lx,Ly,スピン配置,周期境界)
    #ls = 隣接格子点(ix,iy,Lx,Ly,周期境界)
    S = 0
    if ix == 1
        left = スピン配置[Lx,iy]
    else
        left = スピン配置[ix-1,iy]
    end
    if ix == Lx
        right = スピン配置[1,iy]
    else
        right = スピン配置[ix+1,iy]
    end
    if iy == 1
        down = スピン配置[ix,Ly]
    else
        down = スピン配置[ix,iy-1]
    end
    if iy == Ly
        up = スピン配置[ix,1]
    else
        up = スピン配置[ix,iy+1]
    end

    S = (left+right+down+up)

    return S
end

周辺スピン和 (generic function with 1 method)

で計算してみよう。その結果、あるスピン配置における全エネルギーは

In [3]:
function 全エネルギー(スピン配置,周期境界,J,h)
    Lx = size(スピン配置,1)
    Ly = size(スピン配置,2)        
    E = 0.0
    for ix in 1:Lx
        for iy in 1:Ly
            σi = スピン配置[ix,iy]
            S = 周辺スピン和(ix,iy,Lx,Ly,スピン配置,周期境界)            
            E += -(J/2)*σi*S-h*σi
        end
    end
    return E
end

全エネルギー (generic function with 1 method)

とかける。  
書いた当初は隣接格子点という関数を読んで周辺スピン和の計算を行っていたが、そのまま書いたほうが3倍速かったので、隣接格子点という関数は使わないことにした。
### メトロポリス法
あるサイトをランダムに選び、そのスピンをフリップさせることでスピン配置を更新するとする。
この時、全サイト数を$N = L_x \times L_y$とすると、確率$1/N$でサイト数を選ぶ。そして、このようなスピンフリップであればプロセスは対称であるので、メトロポリス法でのある配置$C_i$から$C_j$への採択率は
これは
$$
A(C_i \rightarrow C_j)  = {\rm min} \left(1, \frac{P(C_j)}{P(C_i)}\right)
$$
となる。ここで、$P(C_i)$をボルツマン重み
$$
P(C_i) = \exp \left( -\frac{H({\cal C}_i)}{k_{\rm B} T} \right)
$$
と選べば、物理量を重みつきモンテカルロ法で計算できる。  
スピン配置${\cal C}_k$のあるサイト${\bf i}$のスピン$\sigma_{\bf i}$をフリップさせスピン配置${\cal C}_k'$とする時、
採択率に現れる重みの比は
$$
\frac{P(C_k')}{P(C_k)} = \exp \left( -\frac{(H({\cal C}_k)-H({\cal C}_k'))}{k_{\rm B} T} \right)
$$
$$
= \exp \left( -\frac{\Delta E({\cal C}_k,{\bf i})}{k_{\rm B} T}\right)
$$
となる。  
よって、エネルギー差$\Delta E$が与えられた時、メトロポリス法は

In [4]:
function メトロポリス法!(σi,ΔE,T,E,mz)
    σ_new = ifelse(rand() <= exp(-ΔE/T),-σi,σi)
    E,mz,accept = ifelse(σ_new == -σi,(E+ΔE,mz-2*σi,1),(E,mz,0))
    return σ_new,E,accept,mz
end

メトロポリス法! (generic function with 1 method)

となる。ここで、フリップしたスピンが受け入れられた時、そのエネルギー$E$、全体磁化$m_z$を計算している。
### 熱浴法
熱浴法では、遷移確率は条件付き確率で計算される。
ランダムにサイトが選ばれる場合の条件付き確率を考えよう。
ランダムに選んだサイト${\bf i}$でのスピン状態を$\sigma_{\bf i}$、それ以外のサイトのスピン状態を${\bf \sigma}({\cal C}_{k,{\bf i/}})$とする。
このスピン配置${\cal C}_k$は${\cal C}_k = (\sigma_{\bf i},{\bf \sigma}({\cal C}_{k,{\bf i/}}))$とおける。
サイト${\bf i}$以外のスピン配置が${\bf \sigma}({\cal C}_{k,{\bf i/}})$の時、サイト${\bf i}$でスピン状態$\sigma_{\bf i}$が選ばれる条件付き確率を$P(\sigma_{\bf i}|{\bf \sigma}({\cal C}_{k,{\bf i/}}))$すれば、
スピン配置${\cal C}_k = (\sigma_{\bf i},{\bf \sigma}({\cal C}_{k,{\bf i/}}))$から
${\cal C}_k' = (+1,{\bf \sigma}({\cal C}_{k,{\bf i/}}))$に遷移する確率は
$$
T_{{\cal C}_k \rightarrow {\cal C}_k'} = P(+1|{\bf \sigma}({\cal C}_{k,{\bf i/}}))
$$
である。ここで、条件付き確率は、
$$
P(+1|{\bf \sigma}({\cal C}_{k,{\bf i/}})) = \frac{P((+1,{\bf \sigma}({\cal C}_{k,{\bf i/}})))}{P({\bf \sigma}({\cal C}_{k,{\bf i/}}))}
$$
とかける。ここで、$P({\bf \sigma}({\cal C}_{k,{\bf i/}}))$はスピン配置${\bf \sigma}({\cal C}_{k,{\bf i/}})$が実現する確率で、スピン配置${\bf \sigma}({\cal C}_{k,{\bf i/}})$を持ちサイト${\bf i}$の可能な状態の確率の和となるため、
$$
P({\bf \sigma}({\cal C}_{k,{\bf i/}})) = \sum_{\sigma_{\bf i}=\pm 1} P(\sigma_{\bf i},{\bf \sigma}({\cal C}_{k,{\bf i/}}))
$$
となる。よって、
$$
P(+1|{\bf \sigma}({\cal C}_{k,{\bf i/}}) = \frac{P((+1,{\bf \sigma}({\cal C}_{k,{\bf i/}})))}
{P((+1,{\bf \sigma}({\cal C}_{k,{\bf i/}}))) + P((-1,{\bf \sigma}({\cal C}_{k,{\bf i/}})))
}
$$
$$
 = \frac{1}
{1 + P((-1,{\bf \sigma}({\cal C}_{k,{\bf i/}}))/P((+1,{\bf \sigma}({\cal C}_{k,{\bf i/}}))))}
$$
となる。そして、
$$
P((-1,{\bf \sigma}({\cal C}_{k,{\bf i/}}))/P((+1,{\bf \sigma}({\cal C}_{k,{\bf i/}})))) = 
\exp \left( -\frac{\Delta E({\cal C}_k,{\bf i};+1 \rightarrow -1)}{k_{\rm B} T}\right)
$$
となる。ここで、$\Delta E({\cal C}_k,{\bf i};+1 \rightarrow -1)$はサイト${\bf i}$のスピンが$+1$から$-1$となった時のエネルギー差で、
$$
\Delta E({\cal C}_k,{\bf i};+1 \rightarrow -1) = 2J  S_i+ 2h = \Delta E({\cal C}_k,{\bf i}) \sigma_{\bf i}
$$
となる。  
少し式を整理すると、熱浴法におけるサイト${\bf i}$のスピンが$+1$になる確率は
$$
T_{{\cal C}_k \rightarrow {\cal C}_k'} = \frac{1}{2}\left( 1 + \tanh \left( -\frac{\Delta E({\cal C}_k,{\bf i};+1 \rightarrow -1)}{2k_{\rm B} T}\right) \right)
$$
となる。つまり、一様乱数$r$がこの値以下であればスピンを$+1$に、そうでなけば$-1$にすればよい。  
以上より、熱浴法を実行する関数は

In [5]:
function 熱浴法!(σi,ΔE,T,E,mz)
    α = σi*ΔE
    ratio = (1 + tanh(α/2T))/2 #アップスピンの受け入れ確率    
    σ_new = ifelse(rand() <= ratio,+1,-1)
    E,mz,accept = ifelse(σ_new == -σi,(ΔE,-2*σi,1),(E,mz,0))
    return σ_new,E,accept,mz    
end

熱浴法! (generic function with 1 method)

そして、ランダムにサイト${\bf i}$を選び、配置のアップデートを試みる関数は

In [6]:
function 配置アップデート!(スピン配置,周期境界,flipmethod,T,J,h,E,mz)
    Lx = size(スピン配置,1)
    Ly = size(スピン配置,2)    
    ix = rand(1:Lx)
    iy = rand(1:Ly)  
    σi = スピン配置[ix,iy]
    S = 周辺スピン和(ix,iy,Lx,Ly,スピン配置,周期境界)
    ΔE =  2J*σi*S+2h*σi
    スピン配置[ix,iy],E,accept,mz = flipmethod(σi,ΔE,T,E,mz)
    #println(accept)
    return スピン配置,E,mz,accept
end

配置アップデート! (generic function with 1 method)

となる。ここで、メトロポリス法と熱浴法の両方を選んで用いたいので、flipmethodという関数を引数とした。  
### モンテカルロ法
以上より、モンテカルロ法の関数は

In [7]:
using ProgressMeter
function モンテカルロ法!(スピン配置,周期境界,flipmethod,T,J,h,最大ステップ,熱化ステップ)
    prog = Progress(最大ステップ,1)
    E = 全エネルギー(スピン配置,周期境界,J,h)
    mz = sum(スピン配置)
    accept = 0
    受けいれ総数 = 0
    totalcount = 最大ステップ-熱化ステップ
    Mz = Array{Float64}(totalcount)
    Energy = Array{Float64}(totalcount)
    比熱 = Array{Float64}(totalcount)
    受けいれ確率 = Array{Float64}(totalcount)
    Mz2 = Array{Float64}(totalcount) #磁化の二乗
    mzヒストグラム = zeros(Int64,length(スピン配置)*2+1)
    mzsum = 0.0
    mz2sum = 0.0
    energy = 0.0
    energy2 = 0.0
    count = 0
    for i=1:最大ステップ
        for j=1:length(スピン配置)
            スピン配置,E,mz,accept = 配置アップデート!(スピン配置,周期境界,flipmethod,T,J,h,E,mz) 
        end
        if rand() < 0.01            
            スピン配置 = -スピン配置
            mz = -mz
            accept = 1
        end
        if i > 熱化ステップ 
            mzヒストグラム[mz+length(スピン配置)+1] += 1
            count += 1 
            mzsum += mz/length(スピン配置) 
            mz2sum += (mz/length(スピン配置))^2             
            energy += E
            energy2 += E^2
            受けいれ総数 += accept 
            Mz[count] = mzsum/count
            Mz2[count] = mz2sum/count            
            Energy[count] = energy/count
            比熱[count] = (energy2/count-Energy[count]^2)/T^2
            受けいれ確率[count] = 受けいれ総数/count
        end 
        next!(prog)
    end
    return Mz[1:count],Mz2[1:count],Energy[1:count],比熱[1:count],受けいれ確率[1:count],mzヒストグラム

end

using Plots





となる。 
関数の中では、時々全反転をするようにしている。また、格子点の数だけフリップを試みることを「1モンテカルロステップ」と呼び、スピンフリップの回数は「最大ステップ」$\times$LxLyとなる。
### シミュレーション
さて、実際に計算してみよう。  
まず、二次元イジング模型には$h=0$での厳密解が存在しており、強磁性転移の温度$T_c$は
$$
T_c = \frac{2J}{\ln (1 + \sqrt{2})}
$$

In [8]:
Tc = 2/log(1+sqrt(2))

2.269185314213022

である。この温度より低いと、強磁性相となる。  
まず、磁化のヒストグラムを見てみよう。毎回毎回に磁化がどのような値になっているかを見る。転移温度以下の場合、格子点あたりの磁化は$+1$と$-1$に偏るはずである。  
転移温度以下の場合、

In [9]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 10000
熱化ステップ = 200

T = 1.0   
J = 1.0
h = 0.0
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,J,h,最大ステップ,熱化ステップ)
time = Int64[]
for i in 1:length(mzヒストグラム)
    push!(time,i-Lx*Ly-1)
end 
plot(time./(Lx*Ly),mzヒストグラム)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 0 
 
 
 250 
 
 
 500 
 
 
 750 
 
 
 1000 
 
<polyline clip-path="url(#clip5402)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 42.1066,309.313 42.1335,375.813 42.1604,175.962 42.1873,375.813 42.2142,52.7613 42.2411,375.813 42.268,11.811 42.2949,375.813 42.3218,21.6111 42.3487,375.813 
 42.3757,123.462 42.4026,375.813 42.4295,206.762 42.4564,375.813 42.4833,284.113 42.5102,375.813 42.5371,329.963 42.564,375.813 42.5909,356.913 42.6178,375.813 
 42.6448,365.663 42.6717,375.813 42.6986,370.913 42.7255,375.813 42.7524,374.763 42.7793,375.813 42.8062,375.113 42.8331,375.813 42.86,375.463 42.887,375.813 
 42.9139,375.813 42.9408,375.813 42.9677,375.813 42.9946,375.813 43.0215,375.813 43.0484,375.813 43.0753,375.463 43.1022,375.813 43.1291,375.813 43.1561,375.813 
 43.183,375.813 43.2099,375.813 43.2368,375.813 43.2637,375.813 43.2906,375.813 43.3175,375.813 43.3444,375.813 43.3713,375.813 43.3983,374.763 43.4252,375.813 
 43.4521,375.813 43.479,375.813 43.5059,375.813 43.5328,375.813 43.5597,375.813 43.5866,375.813 43.6135,375.463 43.6404,375.813 43.6674,375.813 43.6943,375.813 
 43.7212,375.813 43.7481,375.813 43.775,375.813 43.8019,375.813 43.8288,375.813 43.8557,375.813 43.8826,375.813 43.9095,375.813 43.9365,375.463 43.9634,375.813 
 43.9903,375.813 44.0172,375.813 44.0441,375.463 44.071,375.813 44.0979,375.113 44.1248,375.813 44.1517,375.463 44.1787,375.813 44.2056,375.813 44.2325,375.813 
 44.2594,375.463 44.2863,375.813 44.3132,375.813 44.3401,375.813 44.367,375.813 44.3939,375.813 44.4208,375.813 44.4478,375.813 44.4747,375.813 44.5016,375.813 
 44.5285,375.813 44.5554,375.813 44.5823,375.463 44.6092,375.813 44.6361,375.813 44.663,375.813 44.69,375.813 44.7169,375.813 44.7438,375.813 44.7707,375.813 
 44.7976,375.813 44.8245,375.813 44.8514,375.813 44.8783,375.813 44.9052,375.813 44.9321,375.813 44.9591,375.813 44.986,375.813 45.0129,375.463 45.0398,375.813 
 45.0667,375.813 45.0936,375.813 45.1205,375.813 45.1474,375.813 45.1743,375.813 45.2012,375.813 45.2282,375.813 45.2551,375.813 45.282,375.813 45.3089,375.813 
 45.3358,375.813 45.3627,375.813 45.3896,375.813 45.4165,375.813 45.4434,375.463 45.4704,375.813 45.4973,375.813 45.5242,375.813 45.5511,375.813 45.578,375.813 
 45.6049,375.463 45.6318,375.813 45.6587,375.813 45.6856,375.813 45.7125,375.813 45.7395,375.813 45.7664,375.813 45.7933,375.813 45.8202,375.813 45.8471,375.813 
 45.874,375.813 45.9009,375.813 45.9278,375.813 45.9547,375.813 45.9817,375.813 46.0086,375.813 46.0355,375.813 46.0624,375.813 46.0893,375.813 46.1162,375.813 
 46.1431,375.813 46.17,375.813 46.1969,375.813 46.2238,375.813 46.2508,375.813 46.2777,375.813 46.3046,375.813 46.3315,375.813 46.3584,375.813 46.3853,375.813 
 46.4122,375.813 46.4391,375.813 46.466,375.813 46.4929,375.813 46.5199,375.813 46.5468,375.813 46.5737,375.813 46.6006,375.813 46.6275,375.813 46.6544,375.813 
 46.6813,375.813 46.7082,375.813 46.7351,375.813 46.7621,375.813 46.789,375.813 46.8159,375.813 46.8428,375.813 46.8697,375.813 46.8966,375.813 46.9235,375.813 
 46.9504,375.813 46.9773,375.813 47.0042,375.813 47.0312,375.813 47.0581,375.813 47.085,375.813 47.1119,375.813 47.1388,375.813 47.1657,375.813 47.1926,375.813 
 47.2195,375.813 47.2464,375.813 47.2734,375.813 47.3003,375.813 47.3272,375.813 47.3541,375.813 47.381,375.813 47.4079,375.813 47.4348,375.813 47.4617,375.813 
 47.4886,375.813 47.5155,375.813 47.5425,375.813 47.5694,375.813 47.5963,375.813 47.6232,375.813 47.6501,375.813 47.677,375.813 47.7039,375.813 47.7308,375.813 
 47.7577,375.813 47.7846,375.813 47.8116,375.813 47.8385,375.813 47.8654,375.813 47.8923,375.813 47.9192,375.813 47.9461,375.813 47.973,375.813 47.9999,375.813 
 48.0268,375.813 48.0538,375.813 48.0807,375.813 48.1076,375.813 48.1345,375.813 48.1614,375.813 48.1883,375.813 48.2152,375.813

となり、-1と+1に集中していることがわかる。つまり、強磁性転移が起きている。
#### 計算の高速化
さて、この計算は手元のパソコンで1分ほどで終わった。しかし、どうやらこれよりも高速化できるようである。Twitterで@kikumacoさんから教わった方法はもっと速いようである。  
まず、乱数の中で無数にif文を呼ぶのは、どんな言語でも明らかに遅そうである。よって、ここを改良する。

In [10]:
function 周辺スピン和(ix,iy,Lx,Ly,スピン配置,周期境界)
    S = スピン配置[(ix-2+Lx)%Lx+1,iy]+スピン配置[ix%Lx+1,iy]+スピン配置[ix,(iy-2+Ly)%Ly+1]+スピン配置[ix,iy%Ly+1]
    return S
end

周辺スピン和 (generic function with 1 method)

もう一度計算してみよう。

In [11]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 10000
熱化ステップ = 200

T = 1.0   
J = 1.0
h = 0.0
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,J,h,最大ステップ,熱化ステップ)
time = Int64[]
for i in 1:length(mzヒストグラム)
    push!(time,i-Lx*Ly-1)
end 
plot(time./(Lx*Ly),mzヒストグラム)

Progress:  99%|█████████████████████████████████████████|  ETA: 0:00:00

 28.486910 seconds (600.35 M allocations: 11.938 GiB, 4.58% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:00:28


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 0 
 
 
 250 
 
 
 500 
 
 
 750 
 
 
 1000 
 
<polyline clip-path="url(#clip5602)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 42.1066,309.313 42.1335,375.813 42.1604,175.962 42.1873,375.813 42.2142,52.7613 42.2411,375.813 42.268,11.811 42.2949,375.813 42.3218,21.6111 42.3487,375.813 
 42.3757,123.462 42.4026,375.813 42.4295,206.762 42.4564,375.813 42.4833,284.113 42.5102,375.813 42.5371,329.963 42.564,375.813 42.5909,356.913 42.6178,375.813 
 42.6448,365.663 42.6717,375.813 42.6986,370.913 42.7255,375.813 42.7524,374.763 42.7793,375.813 42.8062,375.113 42.8331,375.813 42.86,375.463 42.887,375.813 
 42.9139,375.813 42.9408,375.813 42.9677,375.813 42.9946,375.813 43.0215,375.813 43.0484,375.813 43.0753,375.463 43.1022,375.813 43.1291,375.813 43.1561,375.813 
 43.183,375.813 43.2099,375.813 43.2368,375.813 43.2637,375.813 43.2906,375.813 43.3175,375.813 43.3444,375.813 43.3713,375.813 43.3983,374.763 43.4252,375.813 
 43.4521,375.813 43.479,375.813 43.5059,375.813 43.5328,375.813 43.5597,375.813 43.5866,375.813 43.6135,375.463 43.6404,375.813 43.6674,375.813 43.6943,375.813 
 43.7212,375.813 43.7481,375.813 43.775,375.813 43.8019,375.813 43.8288,375.813 43.8557,375.813 43.8826,375.813 43.9095,375.813 43.9365,375.463 43.9634,375.813 
 43.9903,375.813 44.0172,375.813 44.0441,375.463 44.071,375.813 44.0979,375.113 44.1248,375.813 44.1517,375.463 44.1787,375.813 44.2056,375.813 44.2325,375.813 
 44.2594,375.463 44.2863,375.813 44.3132,375.813 44.3401,375.813 44.367,375.813 44.3939,375.813 44.4208,375.813 44.4478,375.813 44.4747,375.813 44.5016,375.813 
 44.5285,375.813 44.5554,375.813 44.5823,375.463 44.6092,375.813 44.6361,375.813 44.663,375.813 44.69,375.813 44.7169,375.813 44.7438,375.813 44.7707,375.813 
 44.7976,375.813 44.8245,375.813 44.8514,375.813 44.8783,375.813 44.9052,375.813 44.9321,375.813 44.9591,375.813 44.986,375.813 45.0129,375.463 45.0398,375.813 
 45.0667,375.813 45.0936,375.813 45.1205,375.813 45.1474,375.813 45.1743,375.813 45.2012,375.813 45.2282,375.813 45.2551,375.813 45.282,375.813 45.3089,375.813 
 45.3358,375.813 45.3627,375.813 45.3896,375.813 45.4165,375.813 45.4434,375.463 45.4704,375.813 45.4973,375.813 45.5242,375.813 45.5511,375.813 45.578,375.813 
 45.6049,375.463 45.6318,375.813 45.6587,375.813 45.6856,375.813 45.7125,375.813 45.7395,375.813 45.7664,375.813 45.7933,375.813 45.8202,375.813 45.8471,375.813 
 45.874,375.813 45.9009,375.813 45.9278,375.813 45.9547,375.813 45.9817,375.813 46.0086,375.813 46.0355,375.813 46.0624,375.813 46.0893,375.813 46.1162,375.813 
 46.1431,375.813 46.17,375.813 46.1969,375.813 46.2238,375.813 46.2508,375.813 46.2777,375.813 46.3046,375.813 46.3315,375.813 46.3584,375.813 46.3853,375.813 
 46.4122,375.813 46.4391,375.813 46.466,375.813 46.4929,375.813 46.5199,375.813 46.5468,375.813 46.5737,375.813 46.6006,375.813 46.6275,375.813 46.6544,375.813 
 46.6813,375.813 46.7082,375.813 46.7351,375.813 46.7621,375.813 46.789,375.813 46.8159,375.813 46.8428,375.813 46.8697,375.813 46.8966,375.813 46.9235,375.813 
 46.9504,375.813 46.9773,375.813 47.0042,375.813 47.0312,375.813 47.0581,375.813 47.085,375.813 47.1119,375.813 47.1388,375.813 47.1657,375.813 47.1926,375.813 
 47.2195,375.813 47.2464,375.813 47.2734,375.813 47.3003,375.813 47.3272,375.813 47.3541,375.813 47.381,375.813 47.4079,375.813 47.4348,375.813 47.4617,375.813 
 47.4886,375.813 47.5155,375.813 47.5425,375.813 47.5694,375.813 47.5963,375.813 47.6232,375.813 47.6501,375.813 47.677,375.813 47.7039,375.813 47.7308,375.813 
 47.7577,375.813 47.7846,375.813 47.8116,375.813 47.8385,375.813 47.8654,375.813 47.8923,375.813 47.9192,375.813 47.9461,375.813 47.973,375.813 47.9999,375.813 
 48.0268,375.813 48.0538,375.813 48.0807,375.813 48.1076,375.813 48.1345,375.813 48.1614,375.813 48.1883,375.813 48.2152,375.813

速くなった。
次に、周辺スピン和に関して、ifelse文を使ってみる。余りを計算するのとどちらが速いか

In [12]:
function 周辺スピン和(ix,iy,Lx,Ly,スピン配置,周期境界)
    S = 0
    jx = ifelse(ix==Lx,1,ix+1)
    jy = iy
    S += スピン配置[jx,jy]
    jx = ifelse(ix==1,Lx,ix-1)
    jy = iy 
    S += スピン配置[jx,jy]
    jy = ifelse(iy==Ly,1,iy+1)
    jx = ix
    S += スピン配置[jx,jy]
    jy = ifelse(iy==1,Ly,iy-1)
    jx = ix 
    S += スピン配置[jx,jy]    
    
    
#    S = スピン配置[(ix-2+Lx)%Lx+1,iy]+スピン配置[ix%Lx+1,iy]+スピン配置[ix,(iy-2+Ly)%Ly+1]+スピン配置[ix,iy%Ly+1]
    return S
end

周辺スピン和 (generic function with 1 method)

In [13]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 10000
熱化ステップ = 200

T = 1.0   
J = 1.0
h = 0.0
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,J,h,最大ステップ,熱化ステップ)
time = Int64[]
for i in 1:length(mzヒストグラム)
    push!(time,i-Lx*Ly-1)
end 
plot(time./(Lx*Ly),mzヒストグラム)

Progress:  99%|████████████████████████████████████████ |  ETA: 0:00:00

 25.459910 seconds (600.35 M allocations: 11.938 GiB, 5.49% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:00:25


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 0 
 
 
 250 
 
 
 500 
 
 
 750 
 
 
 1000 
 
<polyline clip-path="url(#clip5802)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 42.1066,309.313 42.1335,375.813 42.1604,175.962 42.1873,375.813 42.2142,52.7613 42.2411,375.813 42.268,11.811 42.2949,375.813 42.3218,21.6111 42.3487,375.813 
 42.3757,123.462 42.4026,375.813 42.4295,206.762 42.4564,375.813 42.4833,284.113 42.5102,375.813 42.5371,329.963 42.564,375.813 42.5909,356.913 42.6178,375.813 
 42.6448,365.663 42.6717,375.813 42.6986,370.913 42.7255,375.813 42.7524,374.763 42.7793,375.813 42.8062,375.113 42.8331,375.813 42.86,375.463 42.887,375.813 
 42.9139,375.813 42.9408,375.813 42.9677,375.813 42.9946,375.813 43.0215,375.813 43.0484,375.813 43.0753,375.463 43.1022,375.813 43.1291,375.813 43.1561,375.813 
 43.183,375.813 43.2099,375.813 43.2368,375.813 43.2637,375.813 43.2906,375.813 43.3175,375.813 43.3444,375.813 43.3713,375.813 43.3983,374.763 43.4252,375.813 
 43.4521,375.813 43.479,375.813 43.5059,375.813 43.5328,375.813 43.5597,375.813 43.5866,375.813 43.6135,375.463 43.6404,375.813 43.6674,375.813 43.6943,375.813 
 43.7212,375.813 43.7481,375.813 43.775,375.813 43.8019,375.813 43.8288,375.813 43.8557,375.813 43.8826,375.813 43.9095,375.813 43.9365,375.463 43.9634,375.813 
 43.9903,375.813 44.0172,375.813 44.0441,375.463 44.071,375.813 44.0979,375.113 44.1248,375.813 44.1517,375.463 44.1787,375.813 44.2056,375.813 44.2325,375.813 
 44.2594,375.463 44.2863,375.813 44.3132,375.813 44.3401,375.813 44.367,375.813 44.3939,375.813 44.4208,375.813 44.4478,375.813 44.4747,375.813 44.5016,375.813 
 44.5285,375.813 44.5554,375.813 44.5823,375.463 44.6092,375.813 44.6361,375.813 44.663,375.813 44.69,375.813 44.7169,375.813 44.7438,375.813 44.7707,375.813 
 44.7976,375.813 44.8245,375.813 44.8514,375.813 44.8783,375.813 44.9052,375.813 44.9321,375.813 44.9591,375.813 44.986,375.813 45.0129,375.463 45.0398,375.813 
 45.0667,375.813 45.0936,375.813 45.1205,375.813 45.1474,375.813 45.1743,375.813 45.2012,375.813 45.2282,375.813 45.2551,375.813 45.282,375.813 45.3089,375.813 
 45.3358,375.813 45.3627,375.813 45.3896,375.813 45.4165,375.813 45.4434,375.463 45.4704,375.813 45.4973,375.813 45.5242,375.813 45.5511,375.813 45.578,375.813 
 45.6049,375.463 45.6318,375.813 45.6587,375.813 45.6856,375.813 45.7125,375.813 45.7395,375.813 45.7664,375.813 45.7933,375.813 45.8202,375.813 45.8471,375.813 
 45.874,375.813 45.9009,375.813 45.9278,375.813 45.9547,375.813 45.9817,375.813 46.0086,375.813 46.0355,375.813 46.0624,375.813 46.0893,375.813 46.1162,375.813 
 46.1431,375.813 46.17,375.813 46.1969,375.813 46.2238,375.813 46.2508,375.813 46.2777,375.813 46.3046,375.813 46.3315,375.813 46.3584,375.813 46.3853,375.813 
 46.4122,375.813 46.4391,375.813 46.466,375.813 46.4929,375.813 46.5199,375.813 46.5468,375.813 46.5737,375.813 46.6006,375.813 46.6275,375.813 46.6544,375.813 
 46.6813,375.813 46.7082,375.813 46.7351,375.813 46.7621,375.813 46.789,375.813 46.8159,375.813 46.8428,375.813 46.8697,375.813 46.8966,375.813 46.9235,375.813 
 46.9504,375.813 46.9773,375.813 47.0042,375.813 47.0312,375.813 47.0581,375.813 47.085,375.813 47.1119,375.813 47.1388,375.813 47.1657,375.813 47.1926,375.813 
 47.2195,375.813 47.2464,375.813 47.2734,375.813 47.3003,375.813 47.3272,375.813 47.3541,375.813 47.381,375.813 47.4079,375.813 47.4348,375.813 47.4617,375.813 
 47.4886,375.813 47.5155,375.813 47.5425,375.813 47.5694,375.813 47.5963,375.813 47.6232,375.813 47.6501,375.813 47.677,375.813 47.7039,375.813 47.7308,375.813 
 47.7577,375.813 47.7846,375.813 47.8116,375.813 47.8385,375.813 47.8654,375.813 47.8923,375.813 47.9192,375.813 47.9461,375.813 47.973,375.813 47.9999,375.813 
 48.0268,375.813 48.0538,375.813 48.0807,375.813 48.1076,375.813 48.1345,375.813 48.1614,375.813 48.1883,375.813 48.2152,375.813

こちらの方が少し速いようだ。  
しかし、妙にメモリをたくさん使っている。そこで、1スイープを関数にまとめてみよう。

In [14]:
function スイープ!(スピン配置,Lx,Ly,周期境界,flipmethod,T,J,h,E,mz)
    accept = 0
    acc = 0
    for j=1:Lx*Ly
        スピン配置,E,mz,acc = 配置アップデート!(スピン配置,周期境界,flipmethod,T,J,h,E,mz)
        accept += acc
    end
    return スピン配置,E,mz,accept
end

using ProgressMeter
function モンテカルロ法!(スピン配置,周期境界,flipmethod,T,J,h,最大ステップ,熱化ステップ)
    prog = Progress(最大ステップ,1)
    E = 全エネルギー(スピン配置,周期境界,J,h)
    mz = sum(スピン配置)
    accept = 0
    受けいれ総数 = 0
    totalcount = 最大ステップ-熱化ステップ
    Mz = Array{Float64}(totalcount)
    Energy = Array{Float64}(totalcount)
    比熱 = Array{Float64}(totalcount)
    受けいれ確率 = Array{Float64}(totalcount)
    Mz2 = Array{Float64}(totalcount) #磁化の二乗
    mzヒストグラム = zeros(Int64,length(スピン配置)*2+1)
    mzsum = 0.0
    mz2sum = 0.0
    energy = 0.0
    energy2 = 0.0
    count = 0
    Lx = size(スピン配置,1)
    Ly = size(スピン配置,2)
    for i=1:最大ステップ
        スピン配置,E,mz,accept = スイープ!(スピン配置,Lx,Ly,周期境界,flipmethod,T,J,h,E,mz)
        if rand() < 0.01            
            スピン配置 = -スピン配置
            mz = -mz
            accept = 1
        end
        if i > 熱化ステップ 
            mzヒストグラム[mz+length(スピン配置)+1] += 1
            count += 1 
            mzsum += mz/length(スピン配置) 
            mz2sum += (mz/length(スピン配置))^2             
            energy += E
            energy2 += E^2
            受けいれ総数 += accept 
            Mz[count] = mzsum/count
            Mz2[count] = mz2sum/count            
            Energy[count] = energy/count
            比熱[count] = (energy2/count-Energy[count]^2)/T^2
            受けいれ確率[count] = 受けいれ総数/count
        end 
        next!(prog)
    end
    return Mz[1:count],Mz2[1:count],Energy[1:count],比熱[1:count],受けいれ確率[1:count],mzヒストグラム

end

モンテカルロ法! (generic function with 1 method)

In [15]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 10000
熱化ステップ = 200

T = 1.0   
J = 1.0
h = 0.0
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,J,h,最大ステップ,熱化ステップ)
time = Int64[]
for i in 1:length(mzヒストグラム)
    push!(time,i-Lx*Ly-1)
end 
plot(time./(Lx*Ly),mzヒストグラム)

Progress:  99%|█████████████████████████████████████████|  ETA: 0:00:00

 27.350637 seconds (600.54 M allocations: 11.941 GiB, 5.58% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:00:27


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 0 
 
 
 250 
 
 
 500 
 
 
 750 
 
 
 1000 
 
<polyline clip-path="url(#clip6002)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 42.1066,309.313 42.1335,375.813 42.1604,175.962 42.1873,375.813 42.2142,52.7613 42.2411,375.813 42.268,11.811 42.2949,375.813 42.3218,21.6111 42.3487,375.813 
 42.3757,123.462 42.4026,375.813 42.4295,206.762 42.4564,375.813 42.4833,284.113 42.5102,375.813 42.5371,329.963 42.564,375.813 42.5909,356.913 42.6178,375.813 
 42.6448,365.663 42.6717,375.813 42.6986,370.913 42.7255,375.813 42.7524,374.763 42.7793,375.813 42.8062,375.113 42.8331,375.813 42.86,375.463 42.887,375.813 
 42.9139,375.813 42.9408,375.813 42.9677,375.813 42.9946,375.813 43.0215,375.813 43.0484,375.813 43.0753,375.463 43.1022,375.813 43.1291,375.813 43.1561,375.813 
 43.183,375.813 43.2099,375.813 43.2368,375.813 43.2637,375.813 43.2906,375.813 43.3175,375.813 43.3444,375.813 43.3713,375.813 43.3983,374.763 43.4252,375.813 
 43.4521,375.813 43.479,375.813 43.5059,375.813 43.5328,375.813 43.5597,375.813 43.5866,375.813 43.6135,375.463 43.6404,375.813 43.6674,375.813 43.6943,375.813 
 43.7212,375.813 43.7481,375.813 43.775,375.813 43.8019,375.813 43.8288,375.813 43.8557,375.813 43.8826,375.813 43.9095,375.813 43.9365,375.463 43.9634,375.813 
 43.9903,375.813 44.0172,375.813 44.0441,375.463 44.071,375.813 44.0979,375.113 44.1248,375.813 44.1517,375.463 44.1787,375.813 44.2056,375.813 44.2325,375.813 
 44.2594,375.463 44.2863,375.813 44.3132,375.813 44.3401,375.813 44.367,375.813 44.3939,375.813 44.4208,375.813 44.4478,375.813 44.4747,375.813 44.5016,375.813 
 44.5285,375.813 44.5554,375.813 44.5823,375.463 44.6092,375.813 44.6361,375.813 44.663,375.813 44.69,375.813 44.7169,375.813 44.7438,375.813 44.7707,375.813 
 44.7976,375.813 44.8245,375.813 44.8514,375.813 44.8783,375.813 44.9052,375.813 44.9321,375.813 44.9591,375.813 44.986,375.813 45.0129,375.463 45.0398,375.813 
 45.0667,375.813 45.0936,375.813 45.1205,375.813 45.1474,375.813 45.1743,375.813 45.2012,375.813 45.2282,375.813 45.2551,375.813 45.282,375.813 45.3089,375.813 
 45.3358,375.813 45.3627,375.813 45.3896,375.813 45.4165,375.813 45.4434,375.463 45.4704,375.813 45.4973,375.813 45.5242,375.813 45.5511,375.813 45.578,375.813 
 45.6049,375.463 45.6318,375.813 45.6587,375.813 45.6856,375.813 45.7125,375.813 45.7395,375.813 45.7664,375.813 45.7933,375.813 45.8202,375.813 45.8471,375.813 
 45.874,375.813 45.9009,375.813 45.9278,375.813 45.9547,375.813 45.9817,375.813 46.0086,375.813 46.0355,375.813 46.0624,375.813 46.0893,375.813 46.1162,375.813 
 46.1431,375.813 46.17,375.813 46.1969,375.813 46.2238,375.813 46.2508,375.813 46.2777,375.813 46.3046,375.813 46.3315,375.813 46.3584,375.813 46.3853,375.813 
 46.4122,375.813 46.4391,375.813 46.466,375.813 46.4929,375.813 46.5199,375.813 46.5468,375.813 46.5737,375.813 46.6006,375.813 46.6275,375.813 46.6544,375.813 
 46.6813,375.813 46.7082,375.813 46.7351,375.813 46.7621,375.813 46.789,375.813 46.8159,375.813 46.8428,375.813 46.8697,375.813 46.8966,375.813 46.9235,375.813 
 46.9504,375.813 46.9773,375.813 47.0042,375.813 47.0312,375.813 47.0581,375.813 47.085,375.813 47.1119,375.813 47.1388,375.813 47.1657,375.813 47.1926,375.813 
 47.2195,375.813 47.2464,375.813 47.2734,375.813 47.3003,375.813 47.3272,375.813 47.3541,375.813 47.381,375.813 47.4079,375.813 47.4348,375.813 47.4617,375.813 
 47.4886,375.813 47.5155,375.813 47.5425,375.813 47.5694,375.813 47.5963,375.813 47.6232,375.813 47.6501,375.813 47.677,375.813 47.7039,375.813 47.7308,375.813 
 47.7577,375.813 47.7846,375.813 47.8116,375.813 47.8385,375.813 47.8654,375.813 47.8923,375.813 47.9192,375.813 47.9461,375.813 47.973,375.813 47.9999,375.813 
 48.0268,375.813 48.0538,375.813 48.0807,375.813 48.1076,375.813 48.1345,375.813 48.1614,375.813 48.1883,375.813 48.2152,375.813

まだメモリを使っている。もう少しいじってみる。

In [16]:
function スイープ!(スピン配置,Lx,Ly,周期境界,flipmethod,T,J,h,E,mz)
    accept = 0
    acc = 0
    #for j=1:Lx*Ly
    for jx in 1:Lx
        for jy in 1:Ly
            ix = rand(1:Lx)
            iy = rand(1:Ly)          
            σi = スピン配置[ix,iy]    
            S = 周辺スピン和(ix,iy,Lx,Ly,スピン配置,周期境界)
            ΔE =  2J*σi*S+2h*σi
            σ_new,E,acc,mz = flipmethod(σi,ΔE,T,E,mz)            
            スピン配置[ix,iy] = σ_new
            accept += acc
        end
    end
    return スピン配置,E,mz,accept
end


スイープ! (generic function with 1 method)

In [17]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 10000
熱化ステップ = 200

T = 1.0   
J = 1.0
h = 0.0
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,J,h,最大ステップ,熱化ステップ)
time = Int64[]
for i in 1:length(mzヒストグラム)
    push!(time,i-Lx*Ly-1)
end 
plot(time./(Lx*Ly),mzヒストグラム)

Progress:  96%|███████████████████████████████████████  |  ETA: 0:00:00

 11.506572 seconds (437.58 k allocations: 18.585 MiB, 0.05% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:00:11


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 0 
 
 
 250 
 
 
 500 
 
 
 750 
 
 
 1000 
 
<polyline clip-path="url(#clip6202)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 42.1066,309.313 42.1335,375.813 42.1604,175.962 42.1873,375.813 42.2142,52.7613 42.2411,375.813 42.268,11.811 42.2949,375.813 42.3218,21.6111 42.3487,375.813 
 42.3757,123.462 42.4026,375.813 42.4295,206.762 42.4564,375.813 42.4833,284.113 42.5102,375.813 42.5371,329.963 42.564,375.813 42.5909,356.913 42.6178,375.813 
 42.6448,365.663 42.6717,375.813 42.6986,370.913 42.7255,375.813 42.7524,374.763 42.7793,375.813 42.8062,375.113 42.8331,375.813 42.86,375.463 42.887,375.813 
 42.9139,375.813 42.9408,375.813 42.9677,375.813 42.9946,375.813 43.0215,375.813 43.0484,375.813 43.0753,375.463 43.1022,375.813 43.1291,375.813 43.1561,375.813 
 43.183,375.813 43.2099,375.813 43.2368,375.813 43.2637,375.813 43.2906,375.813 43.3175,375.813 43.3444,375.813 43.3713,375.813 43.3983,374.763 43.4252,375.813 
 43.4521,375.813 43.479,375.813 43.5059,375.813 43.5328,375.813 43.5597,375.813 43.5866,375.813 43.6135,375.463 43.6404,375.813 43.6674,375.813 43.6943,375.813 
 43.7212,375.813 43.7481,375.813 43.775,375.813 43.8019,375.813 43.8288,375.813 43.8557,375.813 43.8826,375.813 43.9095,375.813 43.9365,375.463 43.9634,375.813 
 43.9903,375.813 44.0172,375.813 44.0441,375.463 44.071,375.813 44.0979,375.113 44.1248,375.813 44.1517,375.463 44.1787,375.813 44.2056,375.813 44.2325,375.813 
 44.2594,375.463 44.2863,375.813 44.3132,375.813 44.3401,375.813 44.367,375.813 44.3939,375.813 44.4208,375.813 44.4478,375.813 44.4747,375.813 44.5016,375.813 
 44.5285,375.813 44.5554,375.813 44.5823,375.463 44.6092,375.813 44.6361,375.813 44.663,375.813 44.69,375.813 44.7169,375.813 44.7438,375.813 44.7707,375.813 
 44.7976,375.813 44.8245,375.813 44.8514,375.813 44.8783,375.813 44.9052,375.813 44.9321,375.813 44.9591,375.813 44.986,375.813 45.0129,375.463 45.0398,375.813 
 45.0667,375.813 45.0936,375.813 45.1205,375.813 45.1474,375.813 45.1743,375.813 45.2012,375.813 45.2282,375.813 45.2551,375.813 45.282,375.813 45.3089,375.813 
 45.3358,375.813 45.3627,375.813 45.3896,375.813 45.4165,375.813 45.4434,375.463 45.4704,375.813 45.4973,375.813 45.5242,375.813 45.5511,375.813 45.578,375.813 
 45.6049,375.463 45.6318,375.813 45.6587,375.813 45.6856,375.813 45.7125,375.813 45.7395,375.813 45.7664,375.813 45.7933,375.813 45.8202,375.813 45.8471,375.813 
 45.874,375.813 45.9009,375.813 45.9278,375.813 45.9547,375.813 45.9817,375.813 46.0086,375.813 46.0355,375.813 46.0624,375.813 46.0893,375.813 46.1162,375.813 
 46.1431,375.813 46.17,375.813 46.1969,375.813 46.2238,375.813 46.2508,375.813 46.2777,375.813 46.3046,375.813 46.3315,375.813 46.3584,375.813 46.3853,375.813 
 46.4122,375.813 46.4391,375.813 46.466,375.813 46.4929,375.813 46.5199,375.813 46.5468,375.813 46.5737,375.813 46.6006,375.813 46.6275,375.813 46.6544,375.813 
 46.6813,375.813 46.7082,375.813 46.7351,375.813 46.7621,375.813 46.789,375.813 46.8159,375.813 46.8428,375.813 46.8697,375.813 46.8966,375.813 46.9235,375.813 
 46.9504,375.813 46.9773,375.813 47.0042,375.813 47.0312,375.813 47.0581,375.813 47.085,375.813 47.1119,375.813 47.1388,375.813 47.1657,375.813 47.1926,375.813 
 47.2195,375.813 47.2464,375.813 47.2734,375.813 47.3003,375.813 47.3272,375.813 47.3541,375.813 47.381,375.813 47.4079,375.813 47.4348,375.813 47.4617,375.813 
 47.4886,375.813 47.5155,375.813 47.5425,375.813 47.5694,375.813 47.5963,375.813 47.6232,375.813 47.6501,375.813 47.677,375.813 47.7039,375.813 47.7308,375.813 
 47.7577,375.813 47.7846,375.813 47.8116,375.813 47.8385,375.813 47.8654,375.813 47.8923,375.813 47.9192,375.813 47.9461,375.813 47.973,375.813 47.9999,375.813 
 48.0268,375.813 48.0538,375.813 48.0807,375.813 48.1076,375.813 48.1345,375.813 48.1614,375.813 48.1883,375.813 48.2152,375.813

これで、メモリ使用量が激減した。


さらに、磁場がゼロのときは、ΔEが整数なので、あらかじめボルツマン因子を計算しておくことで高速化が期待できる。ここでJでエネルギーの次元を測ることにして、$J=1$とする。

In [18]:
function boltzmann(T)
    w = zeros(Float64,8*2+1)    
    for ΔE in -8:8
        w[ΔE+9] = exp(-ΔE/T)
    end
    return w
end

boltzmann (generic function with 1 method)

Juliaでは、同じ関数名で引数の型や数などが違うものを定義できる（多重ディスパッチ）。したがって、磁場がゼロのときに関数を以下に定義する。

In [54]:
function メトロポリス法!(σi,ΔE,T,E,mz,w)
    σ_new = ifelse(rand() <= w[ΔE+9],-σi,σi)
    E,mz,accept = ifelse(σ_new == -σi,(E+ΔE,mz-2*σi,1),(E,mz,0))
    return σ_new,E,accept,mz
end

function スイープ!(スピン配置,Lx,Ly,周期境界,flipmethod,T,E,mz,w) #磁場hとカップリングJを除去。wを追加
    accept = 0
    acc = 0
    #for j=1:Lx*Ly
    for jx in 1:Lx
        for jy in 1:Ly
            ix = rand(1:Lx)
            iy = rand(1:Ly)          
            σi = スピン配置[ix,iy]    
            S = 周辺スピン和(ix,iy,Lx,Ly,スピン配置,周期境界)
            ΔE =  2σi*S
            σ_new,E,acc,mz = flipmethod(σi,ΔE,T,E,mz,w)#wを追加            
            スピン配置[ix,iy] = σ_new
            accept += acc
        end
    end
    return スピン配置,E,mz,accept
end

スイープ! (generic function with 2 methods)

これを使って、「モンテカルロ法!」を定義する。

In [50]:
function モンテカルロ法!(スピン配置,周期境界,flipmethod,T,最大ステップ,熱化ステップ)
    prog = Progress(最大ステップ,1)
    w = boltzmann(T) #追加した部分
    E = 全エネルギー(スピン配置,周期境界,J,h)
    mz = sum(スピン配置)
    accept = 0
    受けいれ総数 = 0
    totalcount = 最大ステップ-熱化ステップ
    Mz = Array{Float64}(totalcount)
    Energy = Array{Float64}(totalcount)
    比熱 = Array{Float64}(totalcount)
    受けいれ確率 = Array{Float64}(totalcount)
    Mz2 = Array{Float64}(totalcount) #磁化の二乗
    mzヒストグラム = zeros(Int64,length(スピン配置)*2+1)
    mzsum = 0.0
    mz2sum = 0.0
    energy = 0.0
    energy2 = 0.0
    count = 0
    Lx = size(スピン配置,1)
    Ly = size(スピン配置,2)
    for i=1:最大ステップ
        スピン配置,E,mz,accept = スイープ!(スピン配置,Lx,Ly,周期境界,flipmethod,T,E,mz,w)
        if rand() < 0.01            
            スピン配置 = -スピン配置
            mz = -mz
            accept = 1
        end
        if i > 熱化ステップ 
            mzヒストグラム[mz+length(スピン配置)+1] += 1
            count += 1 
            mzsum += mz/length(スピン配置) 
            mz2sum += (mz/length(スピン配置))^2             
            energy += E
            energy2 += E^2
            受けいれ総数 += accept 
            Mz[count] = mzsum/count
            Mz2[count] = mz2sum/count            
            Energy[count] = energy/count
            比熱[count] = (energy2/count-Energy[count]^2)/T^2
            受けいれ確率[count] = 受けいれ総数/count
        end 
        next!(prog)
    end
    return Mz[1:count],Mz2[1:count],Energy[1:count],比熱[1:count],受けいれ確率[1:count],mzヒストグラム

end

モンテカルロ法! (generic function with 2 methods)

この関数を使って、改めて計算すると、

In [21]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 10000
熱化ステップ = 200

T = 1.0   
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,熱化ステップ)
time = Int64[]
for i in 1:length(mzヒストグラム)
    push!(time,i-Lx*Ly-1)
end 
plot(time./(Lx*Ly),mzヒストグラム)

Progress:  34%|██████████████                           |  ETA: 0:00:06

  8.818178 seconds (420.74 k allocations: 18.504 MiB, 0.08% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:00:09


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 0 
 
 
 250 
 
 
 500 
 
 
 750 
 
 
 1000 
 
<polyline clip-path="url(#clip6402)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 42.1066,309.313 42.1335,375.813 42.1604,175.962 42.1873,375.813 42.2142,52.7613 42.2411,375.813 42.268,11.811 42.2949,375.813 42.3218,21.6111 42.3487,375.813 
 42.3757,123.462 42.4026,375.813 42.4295,206.762 42.4564,375.813 42.4833,284.113 42.5102,375.813 42.5371,329.963 42.564,375.813 42.5909,356.913 42.6178,375.813 
 42.6448,365.663 42.6717,375.813 42.6986,370.913 42.7255,375.813 42.7524,374.763 42.7793,375.813 42.8062,375.113 42.8331,375.813 42.86,375.463 42.887,375.813 
 42.9139,375.813 42.9408,375.813 42.9677,375.813 42.9946,375.813 43.0215,375.813 43.0484,375.813 43.0753,375.463 43.1022,375.813 43.1291,375.813 43.1561,375.813 
 43.183,375.813 43.2099,375.813 43.2368,375.813 43.2637,375.813 43.2906,375.813 43.3175,375.813 43.3444,375.813 43.3713,375.813 43.3983,374.763 43.4252,375.813 
 43.4521,375.813 43.479,375.813 43.5059,375.813 43.5328,375.813 43.5597,375.813 43.5866,375.813 43.6135,375.463 43.6404,375.813 43.6674,375.813 43.6943,375.813 
 43.7212,375.813 43.7481,375.813 43.775,375.813 43.8019,375.813 43.8288,375.813 43.8557,375.813 43.8826,375.813 43.9095,375.813 43.9365,375.463 43.9634,375.813 
 43.9903,375.813 44.0172,375.813 44.0441,375.463 44.071,375.813 44.0979,375.113 44.1248,375.813 44.1517,375.463 44.1787,375.813 44.2056,375.813 44.2325,375.813 
 44.2594,375.463 44.2863,375.813 44.3132,375.813 44.3401,375.813 44.367,375.813 44.3939,375.813 44.4208,375.813 44.4478,375.813 44.4747,375.813 44.5016,375.813 
 44.5285,375.813 44.5554,375.813 44.5823,375.463 44.6092,375.813 44.6361,375.813 44.663,375.813 44.69,375.813 44.7169,375.813 44.7438,375.813 44.7707,375.813 
 44.7976,375.813 44.8245,375.813 44.8514,375.813 44.8783,375.813 44.9052,375.813 44.9321,375.813 44.9591,375.813 44.986,375.813 45.0129,375.463 45.0398,375.813 
 45.0667,375.813 45.0936,375.813 45.1205,375.813 45.1474,375.813 45.1743,375.813 45.2012,375.813 45.2282,375.813 45.2551,375.813 45.282,375.813 45.3089,375.813 
 45.3358,375.813 45.3627,375.813 45.3896,375.813 45.4165,375.813 45.4434,375.463 45.4704,375.813 45.4973,375.813 45.5242,375.813 45.5511,375.813 45.578,375.813 
 45.6049,375.463 45.6318,375.813 45.6587,375.813 45.6856,375.813 45.7125,375.813 45.7395,375.813 45.7664,375.813 45.7933,375.813 45.8202,375.813 45.8471,375.813 
 45.874,375.813 45.9009,375.813 45.9278,375.813 45.9547,375.813 45.9817,375.813 46.0086,375.813 46.0355,375.813 46.0624,375.813 46.0893,375.813 46.1162,375.813 
 46.1431,375.813 46.17,375.813 46.1969,375.813 46.2238,375.813 46.2508,375.813 46.2777,375.813 46.3046,375.813 46.3315,375.813 46.3584,375.813 46.3853,375.813 
 46.4122,375.813 46.4391,375.813 46.466,375.813 46.4929,375.813 46.5199,375.813 46.5468,375.813 46.5737,375.813 46.6006,375.813 46.6275,375.813 46.6544,375.813 
 46.6813,375.813 46.7082,375.813 46.7351,375.813 46.7621,375.813 46.789,375.813 46.8159,375.813 46.8428,375.813 46.8697,375.813 46.8966,375.813 46.9235,375.813 
 46.9504,375.813 46.9773,375.813 47.0042,375.813 47.0312,375.813 47.0581,375.813 47.085,375.813 47.1119,375.813 47.1388,375.813 47.1657,375.813 47.1926,375.813 
 47.2195,375.813 47.2464,375.813 47.2734,375.813 47.3003,375.813 47.3272,375.813 47.3541,375.813 47.381,375.813 47.4079,375.813 47.4348,375.813 47.4617,375.813 
 47.4886,375.813 47.5155,375.813 47.5425,375.813 47.5694,375.813 47.5963,375.813 47.6232,375.813 47.6501,375.813 47.677,375.813 47.7039,375.813 47.7308,375.813 
 47.7577,375.813 47.7846,375.813 47.8116,375.813 47.8385,375.813 47.8654,375.813 47.8923,375.813 47.9192,375.813 47.9461,375.813 47.973,375.813 47.9999,375.813 
 48.0268,375.813 48.0538,375.813 48.0807,375.813 48.1076,375.813 48.1345,375.813 48.1614,375.813 48.1883,375.813 48.2152,375.813

20パーセントほど速くなった。  
さて、次にTc以上の温度を見てみよう。

In [22]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 10000
熱化ステップ = 200

T = 3.0   
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,熱化ステップ)
time = Int64[]
for i in 1:length(mzヒストグラム)
    push!(time,i-Lx*Ly-1)
end 
plot(time./(Lx*Ly),mzヒストグラム)

Progress:  99%|█████████████████████████████████████████|  ETA: 0:00:00

  9.115108 seconds (389.03 k allocations: 16.669 MiB, 0.07% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:00:09


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 0 
 
 
 10 
 
 
 20 
 
 
 30 
 
<polyline clip-path="url(#clip6602)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 28.9273,375.813 28.9549,375.813 28.9824,375.813 29.01,375.813 29.0376,375.813 29.0651,375.813 29.0927,375.813 29.1203,375.813 29.1478,375.813 29.1754,375.813 
 29.203,375.813 29.2306,375.813 29.2581,375.813 29.2857,375.813 29.3133,375.813 29.3408,375.813 29.3684,375.813 29.396,375.813 29.4235,375.813 29.4511,375.813 
 29.4787,375.813 29.5062,375.813 29.5338,375.813 29.5614,375.813 29.589,375.813 29.6165,375.813 29.6441,375.813 29.6717,375.813 29.6992,375.813 29.7268,375.813 
 29.7544,375.813 29.7819,375.813 29.8095,375.813 29.8371,375.813 29.8646,375.813 29.8922,375.813 29.9198,375.813 29.9474,375.813 29.9749,375.813 30.0025,375.813 
 30.0301,375.813 30.0576,375.813 30.0852,375.813 30.1128,375.813 30.1403,375.813 30.1679,375.813 30.1955,375.813 30.2231,375.813 30.2506,375.813 30.2782,375.813 
 30.3058,375.813 30.3333,375.813 30.3609,375.813 30.3885,375.813 30.416,375.813 30.4436,375.813 30.4712,375.813 30.4987,375.813 30.5263,375.813 30.5539,375.813 
 30.5815,375.813 30.609,375.813 30.6366,375.813 30.6642,375.813 30.6917,375.813 30.7193,375.813 30.7469,375.813 30.7744,375.813 30.802,375.813 30.8296,375.813 
 30.8571,375.813 30.8847,375.813 30.9123,375.813 30.9399,375.813 30.9674,375.813 30.995,375.813 31.0226,375.813 31.0501,375.813 31.0777,375.813 31.1053,375.813 
 31.1328,375.813 31.1604,375.813 31.188,375.813 31.2155,375.813 31.2431,375.813 31.2707,375.813 31.2983,375.813 31.3258,375.813 31.3534,375.813 31.381,375.813 
 31.4085,375.813 31.4361,375.813 31.4637,375.813 31.4912,375.813 31.5188,375.813 31.5464,375.813 31.574,375.813 31.6015,375.813 31.6291,375.813 31.6567,375.813 
 31.6842,375.813 31.7118,375.813 31.7394,375.813 31.7669,375.813 31.7945,375.813 31.8221,375.813 31.8496,375.813 31.8772,375.813 31.9048,375.813 31.9324,375.813 
 31.9599,375.813 31.9875,375.813 32.0151,375.813 32.0426,375.813 32.0702,375.813 32.0978,375.813 32.1253,375.813 32.1529,375.813 32.1805,375.813 32.208,375.813 
 32.2356,375.813 32.2632,375.813 32.2908,375.813 32.3183,375.813 32.3459,375.813 32.3735,375.813 32.401,375.813 32.4286,375.813 32.4562,375.813 32.4837,375.813 
 32.5113,375.813 32.5389,375.813 32.5664,375.813 32.594,375.813 32.6216,375.813 32.6492,375.813 32.6767,375.813 32.7043,375.813 32.7319,375.813 32.7594,375.813 
 32.787,375.813 32.8146,375.813 32.8421,375.813 32.8697,375.813 32.8973,375.813 32.9249,375.813 32.9524,375.813 32.98,375.813 33.0076,375.813 33.0351,375.813 
 33.0627,375.813 33.0903,375.813 33.1178,375.813 33.1454,375.813 33.173,375.813 33.2005,375.813 33.2281,375.813 33.2557,375.813 33.2833,375.813 33.3108,375.813 
 33.3384,375.813 33.366,375.813 33.3935,375.813 33.4211,375.813 33.4487,375.813 33.4762,375.813 33.5038,375.813 33.5314,375.813 33.5589,375.813 33.5865,375.813 
 33.6141,375.813 33.6417,375.813 33.6692,375.813 33.6968,375.813 33.7244,375.813 33.7519,375.813 33.7795,375.813 33.8071,375.813 33.8346,375.813 33.8622,375.813 
 33.8898,375.813 33.9173,375.813 33.9449,375.813 33.9725,375.813 34.0001,375.813 34.0276,375.813 34.0552,375.813 34.0828,375.813 34.1103,375.813 34.1379,375.813 
 34.1655,375.813 34.193,375.813 34.2206,375.813 34.2482,375.813 34.2758,375.813 34.3033,375.813 34.3309,375.813 34.3585,375.813 34.386,375.813 34.4136,375.813 
 34.4412,375.813 34.4687,375.813 34.4963,375.813 34.5239,375.813 34.5514,375.813 34.579,375.813 34.6066,375.813 34.6342,375.813 34.6617,375.813 34.6893,375.813 
 34.7169,375.813 34.7444,375.813 34.772,375.813 34.7996,375.813 34.8271,375.813 34.8547,375.813 34.8823,375.813 34.9098,375.813 34.9374,375.813 34.965,375.813 
 34.9926,375.813 35.0201,375.813 35.0477,375.813 35.0753,375.813 35.1028,375.813 35.1304,375.813 35.158,375.813 35.1855,375.813 35.2131,375.813 3

磁化の分布が0に集まっており、明らかに有限の磁化はない。  
転移温度ではどうなるだろうか？

In [23]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 10000
熱化ステップ = 200

T = Tc   
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,熱化ステップ)
time = Int64[]
for i in 1:length(mzヒストグラム)
    push!(time,i-Lx*Ly-1)
end 
plot(time./(Lx*Ly),mzヒストグラム)

Progress:  94%|███████████████████████████████████████  |  ETA: 0:00:00

  8.468671 seconds (396.89 k allocations: 16.759 MiB, 0.03% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:00:08


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 0.0 
 
 
 2.5 
 
 
 5.0 
 
 
 7.5 
 
 
 10.0 
 
<polyline clip-path="url(#clip6802)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 38.8117,375.813 38.8388,375.813 38.8659,375.813 38.893,375.813 38.92,375.813 38.9471,375.813 38.9742,375.813 39.0013,375.813 39.0283,375.813 39.0554,375.813 
 39.0825,375.813 39.1096,375.813 39.1366,375.813 39.1637,375.813 39.1908,375.813 39.2179,375.813 39.2449,375.813 39.272,375.813 39.2991,375.813 39.3262,375.813 
 39.3532,375.813 39.3803,375.813 39.4074,375.813 39.4345,375.813 39.4615,375.813 39.4886,375.813 39.5157,375.813 39.5428,375.813 39.5698,375.813 39.5969,375.813 
 39.624,375.813 39.6511,375.813 39.6781,375.813 39.7052,375.813 39.7323,375.813 39.7594,375.813 39.7864,375.813 39.8135,375.813 39.8406,375.813 39.8677,375.813 
 39.8947,375.813 39.9218,375.813 39.9489,375.813 39.976,375.813 40.003,375.813 40.0301,375.813 40.0572,375.813 40.0843,375.813 40.1113,375.813 40.1384,375.813 
 40.1655,375.813 40.1926,375.813 40.2196,375.813 40.2467,375.813 40.2738,375.813 40.3009,375.813 40.3279,375.813 40.355,375.813 40.3821,375.813 40.4092,375.813 
 40.4362,375.813 40.4633,375.813 40.4904,375.813 40.5175,375.813 40.5445,375.813 40.5716,375.813 40.5987,375.813 40.6258,375.813 40.6528,375.813 40.6799,375.813 
 40.707,375.813 40.7341,375.813 40.7611,375.813 40.7882,375.813 40.8153,375.813 40.8424,375.813 40.8694,375.813 40.8965,375.813 40.9236,375.813 40.9507,375.813 
 40.9777,375.813 41.0048,375.813 41.0319,375.813 41.059,375.813 41.086,375.813 41.1131,375.813 41.1402,375.813 41.1673,375.813 41.1943,375.813 41.2214,375.813 
 41.2485,375.813 41.2756,375.813 41.3027,375.813 41.3297,375.813 41.3568,375.813 41.3839,375.813 41.411,375.813 41.438,375.813 41.4651,375.813 41.4922,375.813 
 41.5193,375.813 41.5463,375.813 41.5734,375.813 41.6005,375.813 41.6276,375.813 41.6546,375.813 41.6817,375.813 41.7088,375.813 41.7359,375.813 41.7629,375.813 
 41.79,375.813 41.8171,375.813 41.8442,375.813 41.8712,375.813 41.8983,375.813 41.9254,375.813 41.9525,375.813 41.9795,375.813 42.0066,375.813 42.0337,375.813 
 42.0608,375.813 42.0878,375.813 42.1149,375.813 42.142,375.813 42.1691,375.813 42.1961,375.813 42.2232,375.813 42.2503,375.813 42.2774,375.813 42.3044,375.813 
 42.3315,375.813 42.3586,375.813 42.3857,375.813 42.4127,375.813 42.4398,375.813 42.4669,375.813 42.494,375.813 42.521,375.813 42.5481,375.813 42.5752,375.813 
 42.6023,375.813 42.6293,375.813 42.6564,375.813 42.6835,375.813 42.7106,375.813 42.7376,375.813 42.7647,375.813 42.7918,375.813 42.8189,375.813 42.8459,375.813 
 42.873,375.813 42.9001,375.813 42.9272,375.813 42.9542,375.813 42.9813,375.813 43.0084,375.813 43.0355,375.813 43.0625,375.813 43.0896,375.813 43.1167,375.813 
 43.1438,375.813 43.1708,375.813 43.1979,375.813 43.225,375.813 43.2521,375.813 43.2791,375.813 43.3062,375.813 43.3333,375.813 43.3604,375.813 43.3874,375.813 
 43.4145,375.813 43.4416,375.813 43.4687,375.813 43.4957,375.813 43.5228,375.813 43.5499,375.813 43.577,375.813 43.604,375.813 43.6311,375.813 43.6582,375.813 
 43.6853,375.813 43.7123,375.813 43.7394,375.813 43.7665,375.813 43.7936,375.813 43.8206,375.813 43.8477,375.813 43.8748,375.813 43.9019,375.813 43.9289,375.813 
 43.956,375.813 43.9831,375.813 44.0102,375.813 44.0372,375.813 44.0643,375.813 44.0914,375.813 44.1185,375.813 44.1455,375.813 44.1726,375.813 44.1997,375.813 
 44.2268,375.813 44.2538,375.813 44.2809,375.813 44.308,375.813 44.3351,375.813 44.3621,375.813 44.3892,375.813 44.4163,375.813 44.4434,375.813 44.4704,375.813 
 44.4975,375.813 44.5246,375.813 44.5517,375.813 44.5787,375.813 44.6058,375.813 44.6329,375.813 44.66,375.813 44.687,375.813 44.7141,375.813 44.7412,375.813 
 44.7683,375.813 44.7953,375.813 44.8224,375.813 44.8495,375.813 44.8766,375.813 44.9036,375.813 44.9307,375.813 44.9578,375.81

ヒストグラムがギザギザしていて、サンプル数が足りない感じになっている。したがって、サンプル数を10倍増やしてみよう。

In [24]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 100000
熱化ステップ = 200

T = Tc   
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,熱化ステップ)
time = Int64[]
for i in 1:length(mzヒストグラム)
    push!(time,i-Lx*Ly-1)
end 
plot(time./(Lx*Ly),mzヒストグラム)

Progress: 100%|█████████████████████████████████████████|  ETA: 0:00:00

 82.377186 seconds (4.06 M allocations: 163.545 MiB, 0.03% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:01:22


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 0 
 
 
 10 
 
 
 20 
 
 
 30 
 
 
 40 
 
 
 50 
 
 
 60 
 
<polyline clip-path="url(#clip7002)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 28.9273,375.813 28.9549,375.813 28.9824,375.813 29.01,375.813 29.0376,375.813 29.0651,375.813 29.0927,375.813 29.1203,375.813 29.1478,375.813 29.1754,375.813 
 29.203,375.813 29.2306,375.813 29.2581,375.813 29.2857,375.813 29.3133,375.813 29.3408,375.813 29.3684,375.813 29.396,375.813 29.4235,375.813 29.4511,375.813 
 29.4787,375.813 29.5062,375.813 29.5338,375.813 29.5614,375.813 29.589,375.813 29.6165,375.813 29.6441,375.813 29.6717,375.813 29.6992,375.813 29.7268,375.813 
 29.7544,375.813 29.7819,375.813 29.8095,375.813 29.8371,375.813 29.8646,375.813 29.8922,375.813 29.9198,375.813 29.9474,375.813 29.9749,375.813 30.0025,375.813 
 30.0301,375.813 30.0576,375.813 30.0852,375.813 30.1128,375.813 30.1403,375.813 30.1679,375.813 30.1955,375.813 30.2231,375.813 30.2506,375.813 30.2782,375.813 
 30.3058,375.813 30.3333,375.813 30.3609,375.813 30.3885,375.813 30.416,375.813 30.4436,375.813 30.4712,375.813 30.4987,375.813 30.5263,375.813 30.5539,375.813 
 30.5815,375.813 30.609,375.813 30.6366,375.813 30.6642,375.813 30.6917,375.813 30.7193,375.813 30.7469,375.813 30.7744,375.813 30.802,375.813 30.8296,375.813 
 30.8571,375.813 30.8847,375.813 30.9123,375.813 30.9399,375.813 30.9674,375.813 30.995,375.813 31.0226,375.813 31.0501,375.813 31.0777,375.813 31.1053,375.813 
 31.1328,375.813 31.1604,375.813 31.188,375.813 31.2155,375.813 31.2431,375.813 31.2707,375.813 31.2983,375.813 31.3258,375.813 31.3534,375.813 31.381,375.813 
 31.4085,375.813 31.4361,375.813 31.4637,375.813 31.4912,375.813 31.5188,375.813 31.5464,375.813 31.574,375.813 31.6015,375.813 31.6291,375.813 31.6567,375.813 
 31.6842,375.813 31.7118,375.813 31.7394,375.813 31.7669,375.813 31.7945,375.813 31.8221,375.813 31.8496,375.813 31.8772,375.813 31.9048,375.813 31.9324,375.813 
 31.9599,375.813 31.9875,375.813 32.0151,375.813 32.0426,375.813 32.0702,375.813 32.0978,375.813 32.1253,375.813 32.1529,375.813 32.1805,375.813 32.208,375.813 
 32.2356,375.813 32.2632,375.813 32.2908,375.813 32.3183,375.813 32.3459,375.813 32.3735,375.813 32.401,375.813 32.4286,375.813 32.4562,375.813 32.4837,375.813 
 32.5113,375.813 32.5389,375.813 32.5664,375.813 32.594,375.813 32.6216,375.813 32.6492,375.813 32.6767,375.813 32.7043,375.813 32.7319,375.813 32.7594,375.813 
 32.787,375.813 32.8146,375.813 32.8421,375.813 32.8697,375.813 32.8973,375.813 32.9249,375.813 32.9524,375.813 32.98,375.813 33.0076,375.813 33.0351,375.813 
 33.0627,375.813 33.0903,375.813 33.1178,375.813 33.1454,375.813 33.173,375.813 33.2005,375.813 33.2281,375.813 33.2557,375.813 33.2833,375.813 33.3108,375.813 
 33.3384,375.813 33.366,375.813 33.3935,375.813 33.4211,375.813 33.4487,375.813 33.4762,375.813 33.5038,375.813 33.5314,375.813 33.5589,375.813 33.5865,375.813 
 33.6141,375.813 33.6417,375.813 33.6692,375.813 33.6968,375.813 33.7244,375.813 33.7519,375.813 33.7795,375.813 33.8071,375.813 33.8346,375.813 33.8622,375.813 
 33.8898,375.813 33.9173,375.813 33.9449,375.813 33.9725,375.813 34.0001,375.813 34.0276,375.813 34.0552,375.813 34.0828,375.813 34.1103,375.813 34.1379,375.813 
 34.1655,375.813 34.193,375.813 34.2206,375.813 34.2482,375.813 34.2758,375.813 34.3033,375.813 34.3309,375.813 34.3585,375.813 34.386,375.813 34.4136,375.813 
 34.4412,375.813 34.4687,375.813 34.4963,375.813 34.5239,375.813 34.5514,375.813 34.579,375.813 34.6066,375.813 34.6342,375.813 34.6617,375.813 34.6893,375.813 
 34.7169,375.813 34.7444,375.813 34.772,375.813 34.7996,375.813 34.8271,375.813 34.8547,375.813 34.8823,375.813 34.9098,375.813 34.9374,375.813 34.965,375.813 
 34.9926,375.813 35.0201,375.813 35.0477,375.813 35.0753,375.813 35.1028,375.813 35.1304,375.813 35.158,37

少し分布が綺麗になった。しかし、計算時間がかかるので、もう少し速くしたい。  
乱数の発生が遅い可能性を考え、ランダムに格子点を選ぶのではなく、順番に選んでみよう。また、乱数をif文の中で生成しないようにした。

In [68]:
function メトロポリス法!(σi,ΔE,T,E,mz,w,r)
    σ_new = ifelse(r <= w[ΔE+9],-σi,σi)
    E,mz,accept = ifelse(σ_new == -σi,(E+ΔE,mz-2*σi,1),(E,mz,0))
    return σ_new,E,accept,mz
end


function スイープ!(スピン配置,Lx,Ly,周期境界,flipmethod,T,E,mz,w) #磁場hとカップリングJを除去。wを追加
    r = rand(Lx,Ly)    
    accept = 0
    acc = 0
    #for j=1:Lx*Ly
    for jx in 1:Lx
        for jy in 1:Ly
            ix = jx#rand(1:Lx)
            iy = jy#rand(1:Ly)          
            σi = スピン配置[ix,iy]    
            S = 周辺スピン和(ix,iy,Lx,Ly,スピン配置,周期境界)
            ΔE =  2σi*S
            #σ_new,E,acc,mz = flipmethod(σi,ΔE,T,E,mz,w)#wを追加    
            σ_new,E,acc,mz = flipmethod(σi,ΔE,T,E,mz,w,r[ix,iy])#wを追加             
            スピン配置[ix,iy] = σ_new
            accept += acc
        end
    end
    return スピン配置,E,mz,accept
end



スイープ! (generic function with 2 methods)

In [69]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 100000
熱化ステップ = 200

T = Tc   
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,熱化ステップ)
time = Int64[]
for i in 1:length(mzヒストグラム)
    push!(time,i-Lx*Ly-1)
end 
plot(time./(Lx*Ly),mzヒストグラム)

Progress:  94%|███████████████████████████████████████  |  ETA: 0:00:01

 17.058670 seconds (4.24 M allocations: 7.616 GiB, 4.99% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:00:17


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 0 
 
 
 10 
 
 
 20 
 
 
 30 
 
 
 40 
 
 
 50 
 
 
 60 
 
<polyline clip-path="url(#clip9402)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 28.9273,375.813 28.9549,375.813 28.9824,375.813 29.01,375.813 29.0376,375.813 29.0651,375.813 29.0927,375.813 29.1203,375.813 29.1478,375.813 29.1754,375.813 
 29.203,375.813 29.2306,375.813 29.2581,375.813 29.2857,375.813 29.3133,375.813 29.3408,375.813 29.3684,375.813 29.396,375.813 29.4235,375.813 29.4511,375.813 
 29.4787,375.813 29.5062,375.813 29.5338,375.813 29.5614,375.813 29.589,375.813 29.6165,375.813 29.6441,375.813 29.6717,375.813 29.6992,375.813 29.7268,375.813 
 29.7544,375.813 29.7819,375.813 29.8095,375.813 29.8371,375.813 29.8646,375.813 29.8922,375.813 29.9198,375.813 29.9474,375.813 29.9749,375.813 30.0025,375.813 
 30.0301,375.813 30.0576,375.813 30.0852,375.813 30.1128,375.813 30.1403,375.813 30.1679,375.813 30.1955,375.813 30.2231,375.813 30.2506,375.813 30.2782,375.813 
 30.3058,375.813 30.3333,375.813 30.3609,375.813 30.3885,375.813 30.416,375.813 30.4436,375.813 30.4712,375.813 30.4987,375.813 30.5263,375.813 30.5539,375.813 
 30.5815,375.813 30.609,375.813 30.6366,375.813 30.6642,375.813 30.6917,375.813 30.7193,375.813 30.7469,375.813 30.7744,375.813 30.802,375.813 30.8296,375.813 
 30.8571,375.813 30.8847,375.813 30.9123,375.813 30.9399,375.813 30.9674,375.813 30.995,375.813 31.0226,375.813 31.0501,375.813 31.0777,375.813 31.1053,375.813 
 31.1328,375.813 31.1604,375.813 31.188,375.813 31.2155,375.813 31.2431,375.813 31.2707,375.813 31.2983,375.813 31.3258,375.813 31.3534,375.813 31.381,375.813 
 31.4085,375.813 31.4361,375.813 31.4637,375.813 31.4912,375.813 31.5188,375.813 31.5464,375.813 31.574,375.813 31.6015,375.813 31.6291,375.813 31.6567,375.813 
 31.6842,375.813 31.7118,375.813 31.7394,375.813 31.7669,375.813 31.7945,375.813 31.8221,375.813 31.8496,375.813 31.8772,375.813 31.9048,375.813 31.9324,375.813 
 31.9599,375.813 31.9875,375.813 32.0151,375.813 32.0426,375.813 32.0702,375.813 32.0978,375.813 32.1253,375.813 32.1529,375.813 32.1805,375.813 32.208,375.813 
 32.2356,375.813 32.2632,375.813 32.2908,375.813 32.3183,375.813 32.3459,375.813 32.3735,375.813 32.401,375.813 32.4286,375.813 32.4562,375.813 32.4837,375.813 
 32.5113,375.813 32.5389,375.813 32.5664,375.813 32.594,375.813 32.6216,375.813 32.6492,375.813 32.6767,375.813 32.7043,375.813 32.7319,375.813 32.7594,375.813 
 32.787,375.813 32.8146,375.813 32.8421,375.813 32.8697,375.813 32.8973,375.813 32.9249,375.813 32.9524,375.813 32.98,375.813 33.0076,375.813 33.0351,375.813 
 33.0627,375.813 33.0903,375.813 33.1178,375.813 33.1454,375.813 33.173,375.813 33.2005,375.813 33.2281,375.813 33.2557,375.813 33.2833,375.813 33.3108,375.813 
 33.3384,375.813 33.366,375.813 33.3935,375.813 33.4211,375.813 33.4487,375.813 33.4762,375.813 33.5038,375.813 33.5314,375.813 33.5589,375.813 33.5865,375.813 
 33.6141,375.813 33.6417,375.813 33.6692,375.813 33.6968,375.813 33.7244,375.813 33.7519,375.813 33.7795,375.813 33.8071,375.813 33.8346,375.813 33.8622,375.813 
 33.8898,375.813 33.9173,375.813 33.9449,375.813 33.9725,375.813 34.0001,375.813 34.0276,375.813 34.0552,375.813 34.0828,375.813 34.1103,375.813 34.1379,375.813 
 34.1655,375.813 34.193,375.813 34.2206,375.813 34.2482,375.813 34.2758,375.813 34.3033,375.813 34.3309,375.813 34.3585,375.813 34.386,375.813 34.4136,375.813 
 34.4412,375.813 34.4687,375.813 34.4963,375.813 34.5239,375.813 34.5514,375.813 34.579,375.813 34.6066,375.813 34.6342,375.813 34.6617,375.813 34.6893,375.813 
 34.7169,375.813 34.7444,375.813 34.772,375.813 34.7996,375.813 34.8271,375.813 34.8547,375.813 34.8823,375.813 34.9098,375.813 34.9374,375.813 34.965,375.813 
 34.9926,375.813 35.0201,375.813 35.0477,375.813 35.0753,375.813 35.1028,375.813 35.1304,375.813 35.158,37

さらに高速化できた。  
最後に、100万ステップで計算してみる。

In [70]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 1000000
熱化ステップ = 200

T = Tc   
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,熱化ステップ)
time = Int64[]
for i in 1:length(mzヒストグラム)
    push!(time,i-Lx*Ly-1)
end 
plot(time./(Lx*Ly),mzヒストグラム)

Progress: 100%|█████████████████████████████████████████|  ETA: 0:00:01

170.671098 seconds (42.15 M allocations: 76.154 GiB, 4.69% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:02:51


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 0 
 
 
 100 
 
 
 200 
 
 
 300 
 
 
 400 
 
<polyline clip-path="url(#clip9602)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 35.5169,375.813 35.5442,375.813 35.5714,375.813 35.5986,375.813 35.6259,375.813 35.6531,375.813 35.6804,375.813 35.7076,375.813 35.7348,375.813 35.7621,375.813 
 35.7893,375.813 35.8166,375.813 35.8438,375.813 35.871,375.813 35.8983,375.813 35.9255,375.813 35.9528,375.813 35.98,375.813 36.0072,375.813 36.0345,375.813 
 36.0617,375.813 36.089,375.813 36.1162,375.813 36.1434,375.813 36.1707,375.813 36.1979,375.813 36.2252,375.813 36.2524,375.813 36.2796,375.813 36.3069,375.813 
 36.3341,375.813 36.3614,375.813 36.3886,375.813 36.4158,375.813 36.4431,375.813 36.4703,375.813 36.4976,375.813 36.5248,375.813 36.552,375.813 36.5793,375.813 
 36.6065,375.813 36.6338,375.813 36.661,375.813 36.6882,375.813 36.7155,375.813 36.7427,375.813 36.77,375.813 36.7972,375.813 36.8244,375.813 36.8517,375.813 
 36.8789,375.813 36.9062,375.813 36.9334,375.813 36.9606,375.813 36.9879,375.813 37.0151,375.813 37.0424,375.813 37.0696,375.813 37.0968,375.813 37.1241,375.813 
 37.1513,375.813 37.1786,375.813 37.2058,375.813 37.233,375.813 37.2603,375.813 37.2875,375.813 37.3148,375.813 37.342,375.813 37.3692,375.813 37.3965,375.813 
 37.4237,375.813 37.451,375.813 37.4782,375.813 37.5054,375.813 37.5327,375.813 37.5599,375.813 37.5872,375.813 37.6144,375.813 37.6416,375.813 37.6689,375.813 
 37.6961,375.813 37.7234,375.813 37.7506,375.813 37.7778,375.813 37.8051,375.813 37.8323,375.813 37.8596,375.813 37.8868,375.813 37.914,375.813 37.9413,375.813 
 37.9685,375.813 37.9958,375.813 38.023,375.813 38.0502,375.813 38.0775,375.813 38.1047,375.813 38.132,375.813 38.1592,375.813 38.1864,375.813 38.2137,375.813 
 38.2409,375.813 38.2682,375.813 38.2954,375.813 38.3226,375.813 38.3499,375.813 38.3771,375.813 38.4043,375.813 38.4316,375.813 38.4588,375.813 38.4861,375.813 
 38.5133,375.813 38.5405,375.813 38.5678,375.813 38.595,375.813 38.6223,375.813 38.6495,375.813 38.6767,375.813 38.704,375.813 38.7312,375.813 38.7585,375.813 
 38.7857,375.813 38.8129,375.813 38.8402,375.813 38.8674,375.813 38.8947,375.813 38.9219,375.813 38.9491,375.813 38.9764,375.813 39.0036,375.813 39.0309,375.813 
 39.0581,375.813 39.0853,375.813 39.1126,375.813 39.1398,375.813 39.1671,375.813 39.1943,375.813 39.2215,375.813 39.2488,375.813 39.276,375.813 39.3033,375.813 
 39.3305,375.813 39.3577,375.813 39.385,375.813 39.4122,375.813 39.4395,375.813 39.4667,375.813 39.4939,375.813 39.5212,375.813 39.5484,375.813 39.5757,375.813 
 39.6029,375.813 39.6301,375.813 39.6574,375.813 39.6846,375.813 39.7119,375.813 39.7391,375.813 39.7663,375.813 39.7936,375.813 39.8208,375.813 39.8481,375.813 
 39.8753,375.813 39.9025,375.813 39.9298,375.813 39.957,375.813 39.9843,375.813 40.0115,375.813 40.0387,375.813 40.066,375.813 40.0932,375.813 40.1205,375.813 
 40.1477,375.813 40.1749,375.813 40.2022,375.813 40.2294,375.813 40.2567,375.813 40.2839,375.813 40.3111,375.813 40.3384,375.813 40.3656,375.813 40.3929,375.813 
 40.4201,375.813 40.4473,375.813 40.4746,375.813 40.5018,375.813 40.5291,375.813 40.5563,375.813 40.5835,375.813 40.6108,375.813 40.638,375.813 40.6653,375.813 
 40.6925,375.813 40.7197,375.813 40.747,375.813 40.7742,375.813 40.8015,375.813 40.8287,375.813 40.8559,375.813 40.8832,375.813 40.9104,375.813 40.9377,375.813 
 40.9649,375.813 40.9921,375.813 41.0194,375.813 41.0466,375.813 41.0739,375.813 41.1011,375.813 41.1283,375.813 41.1556,375.813 41.1828,375.813 41.2101,375.813 
 41.2373,375.813 41.2645,375.813 41.2918,375.813 41.319,375.813 41.3463,375.813 41.3735,375.813 41.4007,375.813 41.428,375.813 41.4552,375.813 41.4825,375.813 
 41.5097,375.813 41.5369,375.813 41.5642,375.813 41.5914,375.813 41.6187,375.813 41.6459,375.813 41.6731,375.813 41.7004,375.81

100万ステップでも5分以内に計算することができるようになった。

#### 臨界点近傍の振る舞い
臨界点において、分布にピークが存在している。これは、磁化の絶対値の期待値をとった場合に、有限の値が残ることを意味している。
では、このピークのサイズ依存性はどうなっているだろうか？  
サイズを変化させてプロットしてみる。なお、システムサイズが変わるとヒストグラムのビンのサイズが変わるため（サイズが大きいと一つあたりのビンに入る数が少なくなる）、数がサイズに比例するようにした。

In [71]:
Lx = 50
Ly = 50
最大ステップ = 1000000
熱化ステップ = 200

srand(123)
スピン配置 = rand([-1,1],Lx,Ly)

T = Tc   
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム1 = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,熱化ステップ)
time1 = Int64[]
mzヒストグラム1 = length(mzヒストグラム1)*mzヒストグラム1/sum(mzヒストグラム1)
for i in 1:length(mzヒストグラム1)
    push!(time1,i-Lx*Ly-1)
end 
time1 = time1./(Lx*Ly)
plot(time1,mzヒストグラム1)

Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
 
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム2 = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,熱化ステップ)
mzヒストグラム2 = length(mzヒストグラム2)*mzヒストグラム2/sum(mzヒストグラム2)
time2 = Int64[]
for i in 1:length(mzヒストグラム2)
    push!(time2,i-Lx*Ly-1)
end 
time2 = time2./(Lx*Ly)
plot!(time2,mzヒストグラム2)

Lx = 150
Ly = 150
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)

  
@time Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム3 = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,熱化ステップ)
mzヒストグラム3 = length(mzヒストグラム3)*mzヒストグラム3/sum(mzヒストグラム3)
time3 = Int64[]
for i in 1:length(mzヒストグラム3)
    push!(time3,i-Lx*Ly-1)
end 
time3 = time3./(Lx*Ly)
plot!(time3,mzヒストグラム3)

Progress:  98%|████████████████████████████████████████ |  ETA: 0:00:01

 44.810197 seconds (42.12 M allocations: 19.740 GiB, 5.45% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:00:45
Progress: 100%|█████████████████████████████████████████|  ETA: 0:00:01

171.863945 seconds (42.15 M allocations: 76.154 GiB, 4.57% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:02:52
Progress: 100%|█████████████████████████████████████████|  ETA: 0:00:01

458.226056 seconds (42.39 M allocations: 170.231 GiB, 6.10% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:07:38


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 0.0 
 
 
 2.5 
 
 
 5.0 
 
 
 7.5 
 
 
 10.0 
 
<polyline clip-path="url(#clip9802)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 38.8117,375.813 38.92,375.813 39.0283,375.813 39.1366,375.813 39.2449,375.813 39.3532,375.813 39.4615,375.813 39.5698,375.813 39.6781,375.813 39.7864,375.813 
 39.8947,375.813 40.003,375.813 40.1113,375.813 40.2196,375.813 40.3279,375.813 40.4362,375.813 40.5445,375.813 40.6528,375.813 40.7611,375.813 40.8694,375.813 
 40.9777,375.813 41.086,375.813 41.1943,375.813 41.3027,375.813 41.411,375.813 41.5193,375.813 41.6276,375.813 41.7359,375.813 41.8442,375.813 41.9525,375.813 
 42.0608,375.813 42.1691,375.813 42.2774,375.813 42.3857,375.813 42.494,375.813 42.6023,375.813 42.7106,375.813 42.8189,375.813 42.9272,375.813 43.0355,375.813 
 43.1438,375.813 43.2521,375.813 43.3604,375.813 43.4687,375.813 43.577,375.813 43.6853,375.813 43.7936,375.813 43.9019,375.813 44.0102,375.813 44.1185,375.813 
 44.2268,375.813 44.3351,375.813 44.4434,375.813 44.5517,375.813 44.66,375.813 44.7683,375.813 44.8766,375.813 44.9849,375.813 45.0932,375.813 45.2015,375.813 
 45.3098,375.813 45.4181,375.813 45.5264,375.813 45.6347,375.813 45.743,375.813 45.8513,375.813 45.9596,375.813 46.0679,375.813 46.1762,375.813 46.2845,375.813 
 46.3928,375.813 46.5011,375.813 46.6094,375.813 46.7177,375.813 46.826,375.813 46.9343,375.813 47.0426,375.813 47.1509,375.813 47.2592,375.813 47.3675,375.813 
 47.4758,375.813 47.5841,375.813 47.6924,375.813 47.8007,375.813 47.909,375.813 48.0173,375.813 48.1256,375.813 48.2339,375.813 48.3422,375.813 48.4505,375.813 
 48.5588,375.813 48.6671,375.813 48.7754,375.813 48.8837,375.813 48.992,375.813 49.1003,375.813 49.2086,375.813 49.3169,375.813 49.4252,375.813 49.5335,375.813 
 49.6418,375.813 49.7501,375.813 49.8584,375.813 49.9667,375.813 50.075,375.813 50.1833,375.813 50.2916,375.813 50.3999,375.813 50.5082,375.813 50.6165,375.813 
 50.7248,375.813 50.8331,375.813 50.9414,375.813 51.0497,375.813 51.158,375.813 51.2663,375.813 51.3746,375.813 51.4829,375.813 51.5912,375.813 51.6995,375.813 
 51.8078,375.813 51.9161,375.813 52.0244,375.813 52.1327,375.813 52.241,375.813 52.3493,375.813 52.4576,375.813 52.5659,375.813 52.6742,375.813 52.7825,375.813 
 52.8908,375.813 52.9991,375.813 53.1074,375.813 53.2157,375.813 53.324,375.813 53.4323,375.813 53.5406,375.813 53.6489,375.813 53.7572,375.813 53.8655,375.813 
 53.9738,375.813 54.0821,375.813 54.1904,375.813 54.2987,375.813 54.407,375.813 54.5153,375.813 54.6236,375.813 54.7319,375.813 54.8402,375.813 54.9485,375.813 
 55.0568,375.813 55.1651,375.813 55.2734,375.813 55.3817,375.813 55.49,375.813 55.5983,375.813 55.7066,375.813 55.8149,375.813 55.9232,375.813 56.0315,375.813 
 56.1398,375.813 56.2481,375.813 56.3564,375.813 56.4647,375.813 56.573,375.813 56.6813,375.813 56.7896,375.813 56.8979,375.813 57.0062,375.813 57.1145,375.813 
 57.2228,375.813 57.3311,375.813 57.4394,375.813 57.5477,375.813 57.656,375.813 57.7643,375.813 57.8726,375.813 57.9809,375.813 58.0893,375.813 58.1976,375.813 
 58.3059,375.813 58.4142,375.813 58.5225,375.813 58.6308,375.813 58.7391,375.813 58.8474,375.813 58.9557,375.813 59.064,375.813 59.1723,375.813 59.2806,375.813 
 59.3889,375.813 59.4972,375.813 59.6055,375.813 59.7138,375.813 59.8221,375.813 59.9304,375.813 60.0387,375.813 60.147,375.813 60.2553,375.813 60.3636,375.813 
 60.4719,375.813 60.5802,375.813 60.6885,375.813 60.7968,375.813 60.9051,375.813 61.0134,375.813 61.1217,375.813 61.23,375.813 61.3383,375.813 61.4466,375.813 
 61.5549,375.813 61.6632,375.813 61.7715,375.813 61.8798,375.813 61.9881,375.813 62.0964,375.813 62.2047,375.813 62.313,375.813 62.4213,375.813 62.5296,375.813 
 62.6379,375.813 62.7462,375.813 62.8545,375.813 62.9628,375.813 63.0711,375.813 63.1794,375.813 63.2877,375.813 63.396,375.813

システムサイズが大きくなるに従って、ピークの位置は0に近づいていく。  
それ以外に特徴はあるだろうか？  
実は、臨界温度では、この分布は横軸が$L_{x}^{(-1/8)}$でスケールされるらしい。これを確認してみよう。

In [72]:
Lx = 50
Ly = Lx
plot((time1)*(Lx^(1/8)),mzヒストグラム1,title="1000000 steps",label=string(Lx)*"x"*string(Ly))
Lx = 100
Ly = Lx
plot!((time2)*(Lx^(1/8)),mzヒストグラム2,title="1000000 steps",label=string(Lx)*"x"*string(Ly))
Lx = 150
Ly = Lx
plot!((time3)*(Lx^(1/8)),mzヒストグラム3,title="1000000 steps",label=string(Lx)*"x"*string(Ly))

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.5 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 1.5 
 
 
 0.0 
 
 
 2.5 
 
 
 5.0 
 
 
 7.5 
 
 
 10.0 
 
 
 1000000 steps 
 
<polyline clip-path="url(#clip0002)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 73.5531,375.813 73.6475,375.813 73.7419,375.813 73.8363,375.813 73.9307,375.813 74.0251,375.813 74.1195,375.813 74.2139,375.813 74.3083,375.813 74.4027,375.813 
 74.4971,375.813 74.5915,375.813 74.6859,375.813 74.7803,375.813 74.8747,375.813 74.9691,375.813 75.0635,375.813 75.158,375.813 75.2524,375.813 75.3468,375.813 
 75.4412,375.813 75.5356,375.813 75.63,375.813 75.7244,375.813 75.8188,375.813 75.9132,375.813 76.0076,375.813 76.102,375.813 76.1964,375.813 76.2908,375.813 
 76.3852,375.813 76.4796,375.813 76.574,375.813 76.6684,375.813 76.7628,375.813 76.8572,375.813 76.9516,375.813 77.046,375.813 77.1404,375.813 77.2348,375.813 
 77.3292,375.813 77.4236,375.813 77.5181,375.813 77.6125,375.813 77.7069,375.813 77.8013,375.813 77.8957,375.813 77.9901,375.813 78.0845,375.813 78.1789,375.813 
 78.2733,375.813 78.3677,375.813 78.4621,375.813 78.5565,375.813 78.6509,375.813 78.7453,375.813 78.8397,375.813 78.9341,375.813 79.0285,375.813 79.1229,375.813 
 79.2173,375.813 79.3117,375.813 79.4061,375.813 79.5005,375.813 79.5949,375.813 79.6893,375.813 79.7838,375.813 79.8782,375.813 79.9726,375.813 80.067,375.813 
 80.1614,375.813 80.2558,375.813 80.3502,375.813 80.4446,375.813 80.539,375.813 80.6334,375.813 80.7278,375.813 80.8222,375.813 80.9166,375.813 81.011,375.813 
 81.1054,375.813 81.1998,375.813 81.2942,375.813 81.3886,375.813 81.483,375.813 81.5774,375.813 81.6718,375.813 81.7662,375.813 81.8606,375.813 81.955,375.813 
 82.0495,375.813 82.1439,375.813 82.2383,375.813 82.3327,375.813 82.4271,375.813 82.5215,375.813 82.6159,375.813 82.7103,375.813 82.8047,375.813 82.8991,375.813 
 82.9935,375.813 83.0879,375.813 83.1823,375.813 83.2767,375.813 83.3711,375.813 83.4655,375.813 83.5599,375.813 83.6543,375.813 83.7487,375.813 83.8431,375.813 
 83.9375,375.813 84.0319,375.813 84.1263,375.813 84.2207,375.813 84.3151,375.813 84.4096,375.813 84.504,375.813 84.5984,375.813 84.6928,375.813 84.7872,375.813 
 84.8816,375.813 84.976,375.813 85.0704,375.813 85.1648,375.813 85.2592,375.813 85.3536,375.813 85.448,375.813 85.5424,375.813 85.6368,375.813 85.7312,375.813 
 85.8256,375.813 85.92,375.813 86.0144,375.813 86.1088,375.813 86.2032,375.813 86.2976,375.813 86.392,375.813 86.4864,375.813 86.5808,375.813 86.6753,375.813 
 86.7697,375.813 86.8641,375.813 86.9585,375.813 87.0529,375.813 87.1473,375.813 87.2417,375.813 87.3361,375.813 87.4305,375.813 87.5249,375.813 87.6193,375.813 
 87.7137,375.813 87.8081,375.813 87.9025,375.813 87.9969,375.813 88.0913,375.813 88.1857,375.813 88.2801,375.813 88.3745,375.813 88.4689,375.813 88.5633,375.813 
 88.6577,375.813 88.7521,375.813 88.8465,375.813 88.941,375.813 89.0354,375.813 89.1298,375.813 89.2242,375.813 89.3186,375.813 89.413,375.813 89.5074,375.813 
 89.6018,375.813 89.6962,375.813 89.7906,375.813 89.885,375.813 89.9794,375.813 90.0738,375.813 90.1682,375.813 90.2626,375.813 90.357,375.813 90.4514,375.813 
 90.5458,375.813 90.6402,375.813 90.7346,375.813 90.829,375.813 90.9234,375.813 91.0178,375.813 91.1122,375.813 91.2066,375.813 91.3011,375.813 91.3955,375.813 
 91.4899,375.813 91.5843,375.813 91.6787,375.813 91.7731,375.813 91.8675,375.813 91.9619,375.813 92.0563,375.813 92.1507,375.813 92.2451,375.813 92.3395,375.813 
 92.4339,375.813 92.5283,375.813 92.6227,375.813 92.7171,375.813 92.8115,375.813 92.9059,375.813 93.0003,375.813 93.0947,375.813 93.1891,375.813 93.2835,375.813 
 93.3779,375.813 93.4723,375.813 93.5668,375.813 93.6612,375.813 93.7556,375.813 93.85,375.813 93.9444,375.813 94.0388,375.813 94.1332,375.813 94.2276,375.813 
 94.322,375.813 94.4164,375.813 94.5108,375.813 94.6052,375.813 94.6996,375

綺麗に重なった!

### イジング模型のモンテカルロシミュレーションの可視化
Juliaでは、@animateで簡単にGIFアニメーションファイルを作ることができる。そこで、

In [73]:
function モンテカルロ法可視化!(スピン配置,周期境界,flipmethod,T,最大ステップ,filename)
    E = 全エネルギー(スピン配置,周期境界,J,h)
    w = boltzmann(T) #追加した部分
    mz = sum(スピン配置)
    accept = 0
    prog = Progress(最大ステップ,1)
    
    maps = @animate for i=1:最大ステップ
        スピン配置,E,accept,mz = スイープ!(スピン配置,Lx,Ly,周期境界,flipmethod,T,E,mz,w)
        heatmap(1:Lx, 1:Ly, スピン配置,aspect_ratio=:equal)
        next!(prog)
        end every 100
    gif(maps, "./"*filename, fps = 15)   

end

モンテカルロ法可視化! (generic function with 1 method)

として、スピン配置の発展を見てみよう。  
低温では

In [77]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 10000

T = 1.0   
J = 1.0
filename = "ising_fps15T1.gif"
@time  モンテカルロ法可視化!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,filename)



Progress: 100%|█████████████████████████████████████████| Time: 0:00:21


 21.945034 seconds (58.81 M allocations: 3.786 GiB, 3.78% gc time)


INFO: Saved animation to /Users/nagai/Isingmodel/ising_fps15T1.gif


Plots.AnimatedGif("/Users/nagai/Isingmodel/ising_fps15T1.gif")

臨界温度では

In [78]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 10000

T = Tc   
J = 1.0
filename = "ising_fps15Tc.gif"
@time  モンテカルロ法可視化!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,filename)



Progress: 100%|█████████████████████████████████████████| Time: 0:00:22


 22.960519 seconds (58.83 M allocations: 3.786 GiB, 3.67% gc time)


INFO: Saved animation to /Users/nagai/Isingmodel/ising_fps15Tc.gif


Plots.AnimatedGif("/Users/nagai/Isingmodel/ising_fps15Tc.gif")

高温では

In [80]:
Lx = 100
Ly = 100
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 10000

T = 3.0   
J = 1.0
filename = "ising_fps15T3.gif"
@time  モンテカルロ法可視化!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,filename)



Progress: 100%|█████████████████████████████████████████| Time: 0:00:22


 23.541917 seconds (58.84 M allocations: 3.787 GiB, 3.67% gc time)


INFO: Saved animation to /Users/nagai/Isingmodel/ising_fps15T3.gif


Plots.AnimatedGif("/Users/nagai/Isingmodel/ising_fps15T3.gif")

このように、簡単にシミュレーションが実行できる。  大きさサイズでの振る舞いを見てみよう。低温で、先ほどより長い時間シミュレーションしている。

In [81]:
Lx = 200
Ly = 200
周期境界 = true
srand(123)
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 100000

T = 1.0   
J = 1.0
filename = "ising_fps15T1_200.gif"
@time  モンテカルロ法可視化!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,filename)



Progress: 100%|█████████████████████████████████████████| Time: 0:06:09


378.791396 seconds (823.06 M allocations: 88.898 GiB, 5.27% gc time)


INFO: Saved animation to /Users/nagai/Isingmodel/ising_fps15T1_200.gif


Plots.AnimatedGif("/Users/nagai/Isingmodel/ising_fps15T1_200.gif")

転移温度より低いので、全体が同じスピンの向きに揃っている。

#### 温度依存性
そして、最後に物理量の温度依存性を見てみよう。量としては、磁化の絶対値を見てみる。

In [84]:
srand(123)
Lx = 50
Ly = 50
スピン配置 = rand([-1,1],Lx,Ly)
最大ステップ = 100000
熱化ステップ = 200
Mztdep = Float64[]
比熱tdep = Float64[]
tdep = Float64[]
@time for i in 1:20
    T = (21-i)*0.2
    Mz,Mz2,Energy,比熱,受けいれ確率,mzヒストグラム = モンテカルロ法!(スピン配置,周期境界,メトロポリス法!,T,最大ステップ,熱化ステップ)
    push!(Mztdep,sqrt(Mz2[end]))
    push!(比熱tdep,比熱[end])    
    push!(tdep,T)
end
plot(tdep,Mztdep)

Progress: 100%|█████████████████████████████████████████| Time: 0:00:05
Progress: 100%|█████████████████████████████████████████| Time: 0:00:05
Progress: 100%|█████████████████████████████████████████| Time: 0:00:05
Progress: 100%|█████████████████████████████████████████| Time: 0:00:05
Progress: 100%|█████████████████████████████████████████| Time: 0:00:05
Progress: 100%|█████████████████████████████████████████| Time: 0:00:05
Progress: 100%|█████████████████████████████████████████| Time: 0:00:05
Progress: 100%|█████████████████████████████████████████| Time: 0:00:05
Progress: 100%|█████████████████████████████████████████| Time: 0:00:05
Progress: 100%|█████████████████████████████████████████| Time: 0:00:04
Progress: 100%|█████████████████████████████████████████| Time: 0:00:04
Progress: 100%|█████████████████████████████████████████| Time: 0:00:04
Progress: 100%|█████████████████████████████████████████| Time: 0:00:04
Progress: 100%|█████████████████████████████████████████| Time: 

 87.623169 seconds (82.50 M allocations: 39.453 GiB, 6.65% gc time)


Progress: 100%|█████████████████████████████████████████| Time: 0:00:04


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 0.2 
 
 
 0.4 
 
 
 0.6 
 
 
 0.8 
 
 
 1.0 
 
 
 
 
 
 
 y1

磁化の絶対値はちゃんと転移温度以下で立ち上がっている。比熱は、

In [85]:
plot(tdep,比熱tdep)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 0 
 
 
 1000 
 
 
 2000 
 
 
 3000 
 
 
 
 
 
 
 y1

となり、綺麗なλ転移をしている。

#### おまけ：ベンチマーク
Juliaによる数値計算の速度は、Fortranとどのくらい違うのか？  
http://bb.phys.se.tmu.ac.jp/~bb/pukiwiki/index.php?MCsim  
に二次元イジング模型のFortranコードがあったので、使わせていただくことにする。これをifortでコンパイルして、速度を見てみよう。計算状況は上と同じにする。つまり、熱化ステップを200、ステップ数を100000とする。正確にベンチマークをとったわけではないので、参考ということでみておいてほしい。  
Fortranコードは手動でパラメータを入力する部分があり、そこに数秒ほどかかっているとして、time a.outで測定してみた。



In [95]:
filename = "./dc.dat"
fd = open( filename, "r" )
温度f = zeros(Float64,20)
比熱f = zeros(Float64,20)
磁化f = zeros(Float64,20)
cnt = 0
while !eof(fd) 
    cnt += 1
    line = readline(fd)
    if cnt >3 
        u = split(line)

        温度f[cnt-3] = parse(Float64,u[1])
        比熱f[cnt-3] = parse(Float64,u[3])
        磁化f[cnt-3] = parse(Float64,u[7])
    end
end

plot(温度f,磁化f,marker=:circle,label="Fortran")
plot!(tdep,Mztdep,marker=:circle,label="Julia")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 0.2 
 
 
 0.4 
 
 
 0.6 
 
 
 0.8 
 
 
 1.0 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Fortran 
 
 
 
 
 
 Julia

結果はほとんど一致しているので問題はないだろう。少しずれているのはきになるが、Fortranコードの詳細を読んでいないので、ここでは差異については目をつぶるとする。  
そして、Fortranの計算時間は、インプットする時間を10秒と見積もると、ちょうど100秒ほどであった。  
物理量を測定するタイミングなどによっても速度は変化するので、どちらが速いかははっきり結論付けられないが、JuliaがFortranと同程度のスピードを出していることがわかった。